### Introduction
In this notebook, I use OpenAI chat completions to use gpt 3.5 turbo as an annotator that rates the song lyrics based on the criteria I provide.

In [35]:
import pandas as pd
import openai

In [36]:
# let's first use a subset of the data (with 10 random lyrics) for trial
# I saved this dataset to a csv file in the previous notebook, so let's read that one
df_subset = pd.read_csv('../datasets/lyrics_for_ai_subset.csv', index_col=0)
df_subset.head()

track_lyrics  \
track_id                                                                    
6Q1LtmZPFRGNZbH6VdarBQ  Я испытала огонь и воду\nКрик — моя вторая при...   
551lELbjN8sK1Va8qB71gM  Tenemo' una cuenta pendiente (Contigo)\nNo pod...   
3PqG25cnEC8xQdsO0SkzQF  I know it's hard to tell how mixed up you feel...   
5jNuiCt5KUR808pHv7JRnN  내 눈빛이 말해주고 있어\nLiar, liar, liar, 더 날 속이지마, oh\...   
4jBpZsZ9qx3cZhoEfuKElF  Si ayer no' comiamo' sin las luces\n¿Cómo pued...   

                        gpt_ratings  
track_id                             
6Q1LtmZPFRGNZbH6VdarBQ          NaN  
551lELbjN8sK1Va8qB71gM          NaN  
3PqG25cnEC8xQdsO0SkzQF          NaN  
5jNuiCt5KUR808pHv7JRnN          NaN  
4jBpZsZ9qx3cZhoEfuKElF          NaN

In the code block below, **the content of the first message** is as follows:

"You are a helpful assistant who knows what qualities in lyrics contribute to song popularity. You rate song lyrics in terms of these qualities. If there are swear words, ignore the swear words and rate the lyrics based on the rest. Give your ratings out of 10, where 10 is the highest and 1 is the lowest for each criteria below:

Clear: Lyrics use simple and straightforward language that is easy to understand.

Relatable: Lyrics use universal themes that resonate with a wide audience.

Memorable: Lyrics contain catchy language that is easy to remember.

Engaging: Lyrics weave an engaging narrative with vivid imagery.

Symbolic: Lyrics use rich symbolism and metaphors to convey deeper meanings.

Lyrical: Lyrics exhibit characteristics typical of song lyrics rather than other forms of content.

Happy: Lyrics convey feelings of happiness, playfulness, contentment, acceptance, empowerment, serenity, trust, and optimism.

Surprised: Lyrics convey emotions of surprise, confusion, amazement.

Fearful: Lyrics convey emotions of fear, anxiety, insecurity, rejection, danger.

Angry: Lyrics convey feelings of anger, disappointment, humiliation, bitterness, aggression, frustration, distance, and criticism.

Disgusted: Lyrics convey feelings of disgust, disapproval, disappointment, repulsion, and aversion.

Sad: Lyrics convey emotions of sadness, loneliness, despair, guilt, depression, and hurt.

Return only the 12 ratings as a space delimited list, in the same order as the criteria."


Then the second message is the lyrics to Billie Eilish's 'What was I made for?' The model returns scores, and then the third (user) message is lyrics from the dataframe.

In [52]:
client = openai.OpenAI(api_key="thiswasmysecretkey")

def get_ratings(lyrics):
    print(f"Getting ratings for {lyrics[:40]}") # print the first 40 characters of the lyrics for which ratings are being retrieved
    response = client.chat.completions.create(
      model="gpt-3.5-turbo",
      messages=[
        {
          "role": "system",
          "content": "You are a helpful assistant who knows what qualities in lyrics contribute to song popularity. You rate song lyrics in term of these qualities. If there are swear words, ignore the swear words and rate the lyrics based on the rest. Give your ratings out of 10, where 10 is the highest and 1 is the lowest for each criteria below:\n\nClear: Lyrics use simple and straightforward language that is easy to understand.\n\nRelatable: Lyrics use universal themes that resonate with a wide audience.\n\nMemorable: Lyrics contain catchy language that is easy to remember. \n\nEngaging: Lyrics weave an engaging narrative with vivid imagery.\n\nSymbolic: Lyrics use rich symbolism and metaphors to convey deeper meanings.\n\nLyrical: Lyrics exhibit characteristics typical of song lyrics rather than other forms of content.\n\nHappy: Lyrics convey feelings of happiness, playfulness, contentment, acceptance, empowerment, serenity, trust, and optimism.\n\nSurprised: Lyrics convey emotions of surprise, confusion, amazement.\n\nFearful: Lyrics convey emotions of fear, anxiety, insecurity, rejection, danger.\n\nAngry: Lyrics convey feelings of anger, disappointment, humiliation, bitterness, aggression, frustration, distance, and criticism.\n\nDisgusted: Lyrics convey feelings of disgust, disapproval, disappointment, repulsion, and aversion.\n\nSad: Lyrics convey emotions of sadness, loneliness, despair, guilt, depression, and hurt.\n\nReturn only the 12 ratings as a space delimited list, in the same order as the criteria."
        },
        {
          "role": "user",
          "content": "I used to float, now I just fall down\nI used to know but I'm not sure now\nWhat I was made for\nWhat was I made for?\nTakin' a drive, I was an ideal\nLooked so alive, turns out I'm not real\nJust something you paid for\nWhat was I made for?\n'Cause I, I\nI don't know how to feel\nBut I wanna try\nI don't know how to feel\nBut someday, I might\nSomeday, I might\nWhen did it end? All the enjoyment\nI'm sad again, don't tell my boyfriend\nIt's not what he's made for\nWhat was I made for?\n'Cause I, 'cause I\nI don't know how to feel\nBut I wanna try\nI don't know how to feel\nBut someday I might\nSomeday I might\nThink I forgot how to be happy\nSomething I'm not, but something I can be\nSomething I wait for\nSomething I'm made for\nSomething I'm made for\n"
        },
        {
          "role": "assistant",
          "content": "8 7 8 7 6 8 6 6 4 4 5 7"
        },
        {
          "role": "user",
          "content": lyrics
        }
      ],
      temperature=0.3, # reduces creativity (model returns same scores for the same song on different iterations)
      max_tokens=43, # limits tokens in model's reply
      top_p=0.5, 
      frequency_penalty=0,
      presence_penalty=0
    )
    return response.choices[0].message.content

In [40]:
# applying the function get_ratings to the whole column of 10 songs, 
# I will not use this method with bigger dataset later since we cannot see the progress
df_subset['gpt_ratings'] = df_subset['track_lyrics'].apply(get_ratings)

In [46]:
# we can expand the scores to separate columns like this
# in the playground on OpenAI website, I checked many times that the model gives scores in the same order as the criteria
df_subset[['Clear', 'Relatable', 'Memorable', 'Engaging', 'Symbolic', 'Lyrical', 'Happy', 'Surprised', 
           'Fearful', 'Angry', 'Disgusted', 'Sad']] = df_subset['gpt_ratings'].str.split(' ', expand=True)

In [47]:
df_subset.head(10) # let's see how all the scores look

track_lyrics  \
track_id                                                                    
6Q1LtmZPFRGNZbH6VdarBQ  Я испытала огонь и воду\nКрик — моя вторая при...   
551lELbjN8sK1Va8qB71gM  Tenemo' una cuenta pendiente (Contigo)\nNo pod...   
3PqG25cnEC8xQdsO0SkzQF  I know it's hard to tell how mixed up you feel...   
5jNuiCt5KUR808pHv7JRnN  내 눈빛이 말해주고 있어\nLiar, liar, liar, 더 날 속이지마, oh\...   
4jBpZsZ9qx3cZhoEfuKElF  Si ayer no' comiamo' sin las luces\n¿Cómo pued...   
1sH8XzELvdFPkgJc7wz5Qd  Ooh ooh ooh\n\nLa primera vez que te vi, yea, ...   
6qsArsTq6WoqtUFUe1e15W  The desk where you sit inside of a frame\nMade...   
4Eg0cp8BDbHZOfmxXYJ7Ff  We're going to go on a dive to the deep sea, a...   
6kURXiIFcBrvfh11Soiwqv  I fly in space\nFlying from star to star\nFeel...   
3WbscWz4aaobZf7rt3ap2L  Law hangs by a thread\nHate grows when it’s fe...   

                                    gpt_ratings Clear Relatable Memorable  \
track_id                                                                    
6Q1LtmZPFRGNZbH6VdarBQ  8 5 7 8 8 8 4 4 7 6 6 8     8         5         7   
551lELbjN8sK1Va8qB71gM  6 3 7 6 4 6 3 4 2 2 3 4     6         3         7   
3PqG25cnEC8xQdsO0SkzQF  9 8 9 8 7 9 5 4 3 3 4 8     9         8         9   
5jNuiCt5KUR808pHv7JRnN  7 5 7 6 5 7 3 2 1 1 2 3     7         5         7   
4jBpZsZ9qx3cZhoEfuKElF  6 5 6 6 5 6 3 3 4 4 4 5     6         5         6   
1sH8XzELvdFPkgJc7wz5Qd  8 6 8 7 6 8 7 6 5 4 4 6     8         6         8   
6qsArsTq6WoqtUFUe1e15W  9 8 8 8 7 8 7 7 5 5 6 8     9         8         8   
4Eg0cp8BDbHZOfmxXYJ7Ff  8 9 9 8 7 8 6 4 3 2 4 8     8         9         9   
6kURXiIFcBrvfh11Soiwqv  8 6 7 7 6 8 6 6 5 4 4 6     8         6         7   
3WbscWz4aaobZf7rt3ap2L  9 8 9 9 9 9 2 2 8 8 8 7     9         8         9   

                       Engaging Symbolic Lyrical Happy Surprised Fearful  \
track_id                                                                   
6Q1LtmZPFRGNZbH6VdarBQ        8        8       8     4         4       7   
551lELbjN8sK1Va8qB71gM        6        4       6     3         4       2   
3PqG25cnEC8xQdsO0SkzQF        8        7       9     5         4       3   
5jNuiCt5KUR808pHv7JRnN        6        5       7     3         2       1   
4jBpZsZ9qx3cZhoEfuKElF        6        5       6     3         3       4   
1sH8XzELvdFPkgJc7wz5Qd        7        6       8     7         6       5   
6qsArsTq6WoqtUFUe1e15W        8        7       8     7         7       5   
4Eg0cp8BDbHZOfmxXYJ7Ff        8        7       8     6         4       3   
6kURXiIFcBrvfh11Soiwqv        7        6       8     6         6       5   
3WbscWz4aaobZf7rt3ap2L        9        9       9     2         2       8   

                       Angry Disgusted Sad  
track_id                                    
6Q1LtmZPFRGNZbH6VdarBQ     6         6   8  
551lELbjN8sK1Va8qB71gM     2         3   4  
3PqG25cnEC8xQdsO0SkzQF     3         4   8  
5jNuiCt5KUR808pHv7JRnN     1         2   3  
4jBpZsZ9qx3cZhoEfuKElF     4         4   5  
1sH8XzELvdFPkgJc7wz5Qd     4         4   6  
6qsArsTq6WoqtUFUe1e15W     5         6   8  
4Eg0cp8BDbHZOfmxXYJ7Ff     2         4   8  
6kURXiIFcBrvfh11Soiwqv     4         4   6  
3WbscWz4aaobZf7rt3ap2L     8         8   7

I looked at the English lyrics and the scores make sense.

In [48]:
for index, row in df_subset.iterrows():
    print(row['gpt_ratings'])
    print(row['track_lyrics'])
    print('\n ------- \n')

8 5 7 8 8 8 4 4 7 6 6 8
Я испытала огонь и воду
Крик — моя вторая природа
Я научилась любить и верить
Над моей головой нет Бога
Я на земле в первый раз и в последний
Я не вернусь и я не воскресну
Я обращаю живое в камень
Я извергаю изо рта пламя

Я не боюсь жить, я не боюсь жить

Страх дает мнимую власть
Счастье — голодная пасть
Просто скормлю все мечты
Я теперь ты, я теперь ты
Боль и любовь есть одно
Спорим, ты выберешь зло?
Кровь окропляет цветы
Я снова ты, я снова ты
Страх дает мнимую власть
Счастье — голодная пасть
Просто скормлю все мечты
Я теперь ты, я теперь ты
Боль и любовь есть одно
Спорим, ты выберешь зло?
Кровь окропляет цветы
Я снова ты, я снова ты
See IC3PEAK LiveGet tickets as low as $
Шаг — бездна — твоё сердце

Шаг — бездна — твоё сердце

Я испытала огонь и воду
Крик — моя вторая природа
Я научилась любить и верить
Над моей головой нет бога
Я на земле в первый раз и в последний
Я не вернусь и я не воскресну
Я обращаю живое в камень
Я извергаю изо рта пламя

 ------- 

6

In [70]:
# let's read in the big dataset with all the lyrics
df = pd.read_csv('../datasets/lyrics_for_ai.csv', index_col=0)
df.head()

track_lyrics  \
track_id                                                                    
0r7CVbZTWZgbTCYdfa2P31  Here's to the ones that we got\nCheers to the ...   
1z1Hg7Vb0AhHDiEmnDE79l  Summertime and I'm caught in the feeling\nGett...   
75FpbthrwQmzHlBJLuGdC7  Two kids with their hearts on fire\nWho's gonn...   
1e8PAfcKUYoKkxPhrHqw4x  I'm going under and this time I fear there’s n...   
7fvUMiyapMsRRxr07cU8Ef  L.A. on a Saturday night in the summer\nSundow...   

                        gpt_ratings  
track_id                             
0r7CVbZTWZgbTCYdfa2P31          NaN  
1z1Hg7Vb0AhHDiEmnDE79l          NaN  
75FpbthrwQmzHlBJLuGdC7          NaN  
1e8PAfcKUYoKkxPhrHqw4x          NaN  
7fvUMiyapMsRRxr07cU8Ef          NaN

In [53]:
# the purpose of this code was to see if we can fill the nulls in the larger dataset with the scores already retrieved
# without retrieving the ratings from the gpt again, and it did not work that way as it can be seen from the prints
df_subset['gpt_ratings'] = df_subset['gpt_ratings'].fillna(df_subset['track_lyrics'].apply(get_ratings))

Getting ratings for Я испытала огонь и воду
Крик — моя втора
Getting ratings for Tenemo' una cuenta pendiente (Contigo)
N
Getting ratings for I know it's hard to tell how mixed up yo
Getting ratings for 내 눈빛이 말해주고 있어
Liar, liar, liar, 더 날 속이지마
Getting ratings for Si ayer no' comiamo' sin las luces
¿Cómo
Getting ratings for Ooh ooh ooh

La primera vez que te vi, y
Getting ratings for The desk where you sit inside of a frame
Getting ratings for We're going to go on a dive to the deep 
Getting ratings for I fly in space
Flying from star to star

Getting ratings for Law hangs by a thread
Hate grows when it


In [54]:
df_subset.head(10)

track_lyrics  \
track_id                                                                    
6Q1LtmZPFRGNZbH6VdarBQ  Я испытала огонь и воду\nКрик — моя вторая при...   
551lELbjN8sK1Va8qB71gM  Tenemo' una cuenta pendiente (Contigo)\nNo pod...   
3PqG25cnEC8xQdsO0SkzQF  I know it's hard to tell how mixed up you feel...   
5jNuiCt5KUR808pHv7JRnN  내 눈빛이 말해주고 있어\nLiar, liar, liar, 더 날 속이지마, oh\...   
4jBpZsZ9qx3cZhoEfuKElF  Si ayer no' comiamo' sin las luces\n¿Cómo pued...   
1sH8XzELvdFPkgJc7wz5Qd  Ooh ooh ooh\n\nLa primera vez que te vi, yea, ...   
6qsArsTq6WoqtUFUe1e15W  The desk where you sit inside of a frame\nMade...   
4Eg0cp8BDbHZOfmxXYJ7Ff  We're going to go on a dive to the deep sea, a...   
6kURXiIFcBrvfh11Soiwqv  I fly in space\nFlying from star to star\nFeel...   
3WbscWz4aaobZf7rt3ap2L  Law hangs by a thread\nHate grows when it’s fe...   

                                    gpt_ratings Clear Relatable Memorable  \
track_id                                                                    
6Q1LtmZPFRGNZbH6VdarBQ  8 5 7 8 8 8 4 4 7 6 6 8     8         5         7   
551lELbjN8sK1Va8qB71gM  6 3 7 6 4 6 3 4 2 2 3 4     6         3         7   
3PqG25cnEC8xQdsO0SkzQF  9 8 9 8 7 9 5 4 3 3 4 8     9         8         9   
5jNuiCt5KUR808pHv7JRnN  7 5 7 6 5 7 3 2 1 1 2 3     7         5         7   
4jBpZsZ9qx3cZhoEfuKElF  6 5 6 6 5 6 3 3 4 4 4 5     6         5         6   
1sH8XzELvdFPkgJc7wz5Qd  8 6 8 7 6 8 7 6 5 4 4 6     8         6         8   
6qsArsTq6WoqtUFUe1e15W  9 8 8 8 7 8 7 7 5 5 6 8     9         8         8   
4Eg0cp8BDbHZOfmxXYJ7Ff  8 9 9 8 7 8 6 4 3 2 4 8     8         9         9   
6kURXiIFcBrvfh11Soiwqv  8 6 7 7 6 8 6 6 5 4 4 6     8         6         7   
3WbscWz4aaobZf7rt3ap2L  9 8 9 9 9 9 2 2 8 8 8 7     9         8         9   

                       Engaging Symbolic Lyrical Happy Surprised Fearful  \
track_id                                                                   
6Q1LtmZPFRGNZbH6VdarBQ        8        8       8     4         4       7   
551lELbjN8sK1Va8qB71gM        6        4       6     3         4       2   
3PqG25cnEC8xQdsO0SkzQF        8        7       9     5         4       3   
5jNuiCt5KUR808pHv7JRnN        6        5       7     3         2       1   
4jBpZsZ9qx3cZhoEfuKElF        6        5       6     3         3       4   
1sH8XzELvdFPkgJc7wz5Qd        7        6       8     7         6       5   
6qsArsTq6WoqtUFUe1e15W        8        7       8     7         7       5   
4Eg0cp8BDbHZOfmxXYJ7Ff        8        7       8     6         4       3   
6kURXiIFcBrvfh11Soiwqv        7        6       8     6         6       5   
3WbscWz4aaobZf7rt3ap2L        9        9       9     2         2       8   

                       Angry Disgusted Sad  
track_id                                    
6Q1LtmZPFRGNZbH6VdarBQ     6         6   8  
551lELbjN8sK1Va8qB71gM     2         3   4  
3PqG25cnEC8xQdsO0SkzQF     3         4   8  
5jNuiCt5KUR808pHv7JRnN     1         2   3  
4jBpZsZ9qx3cZhoEfuKElF     4         4   5  
1sH8XzELvdFPkgJc7wz5Qd     4         4   6  
6qsArsTq6WoqtUFUe1e15W     5         6   8  
4Eg0cp8BDbHZOfmxXYJ7Ff     2         4   8  
6kURXiIFcBrvfh11Soiwqv     4         4   6  
3WbscWz4aaobZf7rt3ap2L     8         8   7

In [64]:
# let's try a loop to first check if the ratings are null and then call the function get_ratings
for index, row in df_subset.iterrows():
    if pd.isnull(row['gpt_ratings']): 
        row['gpt_ratings'] = row['track_lyrics'].apply(get_ratings)
    else:
        print('not null so gpt is not called')

not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called
not null so gpt is not called


Since the rows for gpt_ratings are not null, the function get_ratings is not run again (so gpt is not called). But it turns out later that I cannot use apply like this. 

The point of all this is to figure out a way to use the function only when a given cell for gpt_ratings is null. While retrieving the ratings, there might be an error and we might need to start over. So the code for getting the ratings should first check if ratings are missing. 

In [66]:
df_subset.info() # the subset dataset has 10 ratings (so 10 non-nulls)

<class 'pandas.core.frame.DataFrame'>
Index: 10 entries, 6Q1LtmZPFRGNZbH6VdarBQ to 3WbscWz4aaobZf7rt3ap2L
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  10 non-null     object
 1   gpt_ratings   10 non-null     object
 2   Clear         10 non-null     object
 3   Relatable     10 non-null     object
 4   Memorable     10 non-null     object
 5   Engaging      10 non-null     object
 6   Symbolic      10 non-null     object
 7   Lyrical       10 non-null     object
 8   Happy         10 non-null     object
 9   Surprised     10 non-null     object
 10  Fearful       10 non-null     object
 11  Angry         10 non-null     object
 12  Disgusted     10 non-null     object
 13  Sad           10 non-null     object
dtypes: object(14)
memory usage: 1.5+ KB


In [71]:
df.info() # the larger dataset does not have any ratings yet

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   track_lyrics  20072 non-null  object 
 1   gpt_ratings   0 non-null      float64
dtypes: float64(1), object(1)
memory usage: 470.4+ KB


In [72]:
# fill the nulls in the gpt_ratings in the larger dataframe with the corresponding values from the subset dataframe
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_subset['gpt_ratings'])
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   10 non-null     object
dtypes: object(2)
memory usage: 470.4+ KB


Next, I want to get ratings for 100 songs. I will both see how long it takes and how expensive it is from the OpenAI's website.

In [73]:
df_subset_2=df.head(100) # create another subset dataframe with the first hundred rows of the larger dataframe
df_subset_2.info() # examine the dataframe

<class 'pandas.core.frame.DataFrame'>
Index: 100 entries, 0r7CVbZTWZgbTCYdfa2P31 to 0n8ob8S72lvznoVfiwz4qL
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  100 non-null    object
 1   gpt_ratings   0 non-null      object
dtypes: object(2)
memory usage: 2.3+ KB


All of them are null. It seems none of the 10 random rows in the first subset dataframe was from the first 100 rows. 

In [75]:
# let's try another for loop to retrieve ratings for all the nulls
for index, row in df_subset_2.iterrows():
    if pd.isnull(row['gpt_ratings']): 
        row['gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null so gpt is not called') # this should never happen since gpty_ratings all are null

Getting ratings for Here's to the ones that we got
Cheers to
Getting ratings for Summertime and I'm caught in the feeling
Getting ratings for Two kids with their hearts on fire
Who's
Getting ratings for I'm going under and this time I fear the
Getting ratings for L.A. on a Saturday night in the summer
S
Getting ratings for I'm losing my self control
Yeah, you're 
Getting ratings for One more drink, one more Bacardi
One mor
Getting ratings for Weight is on me, weight is on you
We scr
Getting ratings for I can't write one song that's not about 
Getting ratings for She stay trippin', and she crazy, oh no

Getting ratings for I bet you don't kiss her with your eyes 
Getting ratings for Jaja, everybody knows I'm live (Candela)
Getting ratings for Can you hear me? S.O.S
Help me put my mi
Getting ratings for She got the mmm, brown eyes, caramel thi
Getting ratings for All my friends are falling in love
All m
Getting ratings for You've been dressing up the truth
I've b
Getting ratings for Step

In [79]:
df_subset_2.head(20) # from the first 20 rows, it looks like the ratings are not saved to the dataframe

track_lyrics  \
track_id                                                                    
0r7CVbZTWZgbTCYdfa2P31  Here's to the ones that we got\nCheers to the ...   
1z1Hg7Vb0AhHDiEmnDE79l  Summertime and I'm caught in the feeling\nGett...   
75FpbthrwQmzHlBJLuGdC7  Two kids with their hearts on fire\nWho's gonn...   
1e8PAfcKUYoKkxPhrHqw4x  I'm going under and this time I fear there’s n...   
7fvUMiyapMsRRxr07cU8Ef  L.A. on a Saturday night in the summer\nSundow...   
2OAylPUDDfwRGfe0lYqlCQ  I'm losing my self control\nYeah, you're start...   
6b1RNvAcJjQH73eZO4BLAB  One more drink, one more Bacardi\nOne more dan...   
7bF6tCO3gFb8INrEDcjNT5  Weight is on me, weight is on you\nWe scream a...   
1IXGILkPm0tOCNeq00kCPa  I can't write one song that's not about you\nC...   
3eFJI470ALf1EYjywPRsJy  She stay trippin', and she crazy, oh no\nQuit ...   
3iJeF2izF1QcpCgUc97BLl  I bet you don't kiss her with your eyes closed...   
6e0CvGZf7CouOpYF8toXHC  Jaja, everybody knows I'm live (Candela)\nEver...   
3eLdNmnRWr9gIyBcqTSSti  Can you hear me? S.O.S\nHelp me put my mind to...   
1EJgymgJHcjSOGSHcYaxvW  She got the mmm, brown eyes, caramel thighs\nL...   
5WaXMQMlQpq8pwIdaFP43L  All my friends are falling in love\nAll my fri...   
3TjLsDgL0bTbSQIF6M5Ki8  You've been dressing up the truth\nI've been d...   
4QAUGy6k7c3IOAhgWz52r7  Step out into the dawn\nYou pray 'til, you pra...   
3Ciaf6WgvG95TGRGxQ1yO8  4/1\nAriana Grande & Victoria Monet - "MONOPOL...   
2wenGTypSYHXl1sN1pNC7X  If you stay for this minute\nGirl, I'll never ...   
4sqABRRGU7CzcHXCyxUzFw  Do you mean, do you mean what you say?\nWhat y...   

                       gpt_ratings  
track_id                            
0r7CVbZTWZgbTCYdfa2P31         NaN  
1z1Hg7Vb0AhHDiEmnDE79l         NaN  
75FpbthrwQmzHlBJLuGdC7         NaN  
1e8PAfcKUYoKkxPhrHqw4x         NaN  
7fvUMiyapMsRRxr07cU8Ef         NaN  
2OAylPUDDfwRGfe0lYqlCQ         NaN  
6b1RNvAcJjQH73eZO4BLAB         NaN  
7bF6tCO3gFb8INrEDcjNT5         NaN  
1IXGILkPm0tOCNeq00kCPa         NaN  
3eFJI470ALf1EYjywPRsJy         NaN  
3iJeF2izF1QcpCgUc97BLl         NaN  
6e0CvGZf7CouOpYF8toXHC         NaN  
3eLdNmnRWr9gIyBcqTSSti         NaN  
1EJgymgJHcjSOGSHcYaxvW         NaN  
5WaXMQMlQpq8pwIdaFP43L         NaN  
3TjLsDgL0bTbSQIF6M5Ki8         NaN  
4QAUGy6k7c3IOAhgWz52r7         NaN  
3Ciaf6WgvG95TGRGxQ1yO8         NaN  
2wenGTypSYHXl1sN1pNC7X         NaN  
4sqABRRGU7CzcHXCyxUzFw         NaN

In [81]:
df_subset_3 = df_subset_2.head(10) # let's create another subset dataframe with the first 10 rows of subset_2

In [83]:
# this for loop works since we are using .loc and index in line 3, I will use this code to retrieve ratings 
for index, row in df_subset_3.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_subset_3.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null')

Getting ratings for Here's to the ones that we got
Cheers to
Getting ratings for Summertime and I'm caught in the feeling
Getting ratings for Two kids with their hearts on fire
Who's
Getting ratings for I'm going under and this time I fear the
Getting ratings for L.A. on a Saturday night in the summer
S
Getting ratings for I'm losing my self control
Yeah, you're 
Getting ratings for One more drink, one more Bacardi
One mor
Getting ratings for Weight is on me, weight is on you
We scr
Getting ratings for I can't write one song that's not about 
Getting ratings for She stay trippin', and she crazy, oh no



In [84]:
df_subset_3.info() # 10 non-nulls for gpt_ratings shows that the for loop above worked

<class 'pandas.core.frame.DataFrame'>
Index: 10 entries, 0r7CVbZTWZgbTCYdfa2P31 to 3eFJI470ALf1EYjywPRsJy
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  10 non-null     object
 1   gpt_ratings   10 non-null     object
dtypes: object(2)
memory usage: 540.0+ bytes


In [85]:
df_subset_3.head() # let's also check the first 5 rows, scorres are really there, great!

track_lyrics  \
track_id                                                                    
0r7CVbZTWZgbTCYdfa2P31  Here's to the ones that we got\nCheers to the ...   
1z1Hg7Vb0AhHDiEmnDE79l  Summertime and I'm caught in the feeling\nGett...   
75FpbthrwQmzHlBJLuGdC7  Two kids with their hearts on fire\nWho's gonn...   
1e8PAfcKUYoKkxPhrHqw4x  I'm going under and this time I fear there’s n...   
7fvUMiyapMsRRxr07cU8Ef  L.A. on a Saturday night in the summer\nSundow...   

                                    gpt_ratings  
track_id                                         
0r7CVbZTWZgbTCYdfa2P31  9 8 9 8 7 9 7 6 5 4 5 8  
1z1Hg7Vb0AhHDiEmnDE79l  8 6 8 7 5 8 4 6 5 4 5 7  
75FpbthrwQmzHlBJLuGdC7  9 8 9 8 7 9 8 6 5 4 5 8  
1e8PAfcKUYoKkxPhrHqw4x  9 8 9 8 7 9 3 5 2 2 3 9  
7fvUMiyapMsRRxr07cU8Ef  9 8 9 8 7 9 6 4 3 3 4 7

In [86]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_subset_3['gpt_ratings']) # fill the nulls in the larger dataframe
df.info() # there should be 20 non-nulls so far, great

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   20 non-null     object
dtypes: object(2)
memory usage: 470.4+ KB


In [87]:
df_subset_4 = df.head(100) # re-create a smaller dataframe with the first 100 rows of the larger dataframe
df_subset_4.info() # it should have 10 non-nulls, great (the other 10 are somewhere else in the dataframe)

<class 'pandas.core.frame.DataFrame'>
Index: 100 entries, 0r7CVbZTWZgbTCYdfa2P31 to 0n8ob8S72lvznoVfiwz4qL
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  100 non-null    object
 1   gpt_ratings   10 non-null     object
dtypes: object(2)
memory usage: 2.3+ KB


In [88]:
# re-use the for loop tested above to retrieve ratings, this should first print 'not null' 10 times, and it does!
for index, row in df_subset_4.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_subset_4.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null')

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
Getting ratings for I bet you don't kiss her with your eyes 
Getting ratings for Jaja, everybody knows I'm live (Candela)
Getting ratings for Can you hear me? S.O.S
Help me put my mi
Getting ratings for She got the mmm, brown eyes, caramel thi
Getting ratings for All my friends are falling in love
All m
Getting ratings for You've been dressing up the truth
I've b
Getting ratings for Step out into the dawn
You pray 'til, yo
Getting ratings for 4/1
Ariana Grande & Victoria Monet - "MO
Getting ratings for If you stay for this minute
Girl, I'll n
Getting ratings for Do you mean, do you mean what you say?
W
Getting ratings for I've cheated and I've lied
I've broke do
Getting ratings for Do you ever feel like a misfit?
Everythi
Getting ratings for Baby, you're the worst, but
Your worst w
Getting ratings for Oh God, it's the same old song
If I was 
Getting ratings for I miss you pushing me close to the e

In [89]:
df_subset_4.info() # check that there are 100 non-null values in the gpt_ratings column, yes there are!

<class 'pandas.core.frame.DataFrame'>
Index: 100 entries, 0r7CVbZTWZgbTCYdfa2P31 to 0n8ob8S72lvznoVfiwz4qL
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  100 non-null    object
 1   gpt_ratings   100 non-null    object
dtypes: object(2)
memory usage: 6.4+ KB


In [90]:
df_subset_4.head(50) # let's also check that the scores are not all the same numbers or something like that

track_lyrics  \
track_id                                                                    
0r7CVbZTWZgbTCYdfa2P31  Here's to the ones that we got\nCheers to the ...   
1z1Hg7Vb0AhHDiEmnDE79l  Summertime and I'm caught in the feeling\nGett...   
75FpbthrwQmzHlBJLuGdC7  Two kids with their hearts on fire\nWho's gonn...   
1e8PAfcKUYoKkxPhrHqw4x  I'm going under and this time I fear there’s n...   
7fvUMiyapMsRRxr07cU8Ef  L.A. on a Saturday night in the summer\nSundow...   
2OAylPUDDfwRGfe0lYqlCQ  I'm losing my self control\nYeah, you're start...   
6b1RNvAcJjQH73eZO4BLAB  One more drink, one more Bacardi\nOne more dan...   
7bF6tCO3gFb8INrEDcjNT5  Weight is on me, weight is on you\nWe scream a...   
1IXGILkPm0tOCNeq00kCPa  I can't write one song that's not about you\nC...   
3eFJI470ALf1EYjywPRsJy  She stay trippin', and she crazy, oh no\nQuit ...   
3iJeF2izF1QcpCgUc97BLl  I bet you don't kiss her with your eyes closed...   
6e0CvGZf7CouOpYF8toXHC  Jaja, everybody knows I'm live (Candela)\nEver...   
3eLdNmnRWr9gIyBcqTSSti  Can you hear me? S.O.S\nHelp me put my mind to...   
1EJgymgJHcjSOGSHcYaxvW  She got the mmm, brown eyes, caramel thighs\nL...   
5WaXMQMlQpq8pwIdaFP43L  All my friends are falling in love\nAll my fri...   
3TjLsDgL0bTbSQIF6M5Ki8  You've been dressing up the truth\nI've been d...   
4QAUGy6k7c3IOAhgWz52r7  Step out into the dawn\nYou pray 'til, you pra...   
3Ciaf6WgvG95TGRGxQ1yO8  4/1\nAriana Grande & Victoria Monet - "MONOPOL...   
2wenGTypSYHXl1sN1pNC7X  If you stay for this minute\nGirl, I'll never ...   
4sqABRRGU7CzcHXCyxUzFw  Do you mean, do you mean what you say?\nWhat y...   
2M9GeaCQXrV12J0wzBxIwi  I've cheated and I've lied\nI've broke down an...   
4OFFY6L5ywYM1TwhXX69wQ  Do you ever feel like a misfit?\nEverything in...   
1hr5Y2i4NlE3LPvQZ9Q5Ao  Baby, you're the worst, but\nYour worst was st...   
4YaU1EjXIkdRdkOI4cCZys  Oh God, it's the same old song\nIf I was smart...   
0Fc9QSMX6fgEBgDjUax7t7  I miss you pushing me close to the edge\nI mis...   
7AasLZ4TYgh7dbJXZxcZVE  You, you take all of the li-li-light away\nBut...   
4sLtguRBis05qfsBgJ1IdN  Would you love me less? Would you love me less...   
508lUjbGcPrL0CfvHC7UvI  When the morning comes\nWhen we see what we've...   
7FDaS1k08rwMoAThmzUkOZ  It's 4AM, I don't know where to go\nEverywhere...   
6m8SIT10j41SPpPFOknTmP  MEDUZA & Goodboys - Piece Of Your Heart\nAvici...   
5scxjvcdozadBoRRN0UMaM  Don't say you love me 'cause I can't say it ba...   
6oJ6le65B3SEqPwMRNXWjY  Bring me higher love, love\nBring me higher lo...   
2tilX6FUl0IwFgiOYjuc6V  Ah, hmm\nTell me where, tell me where, ah\nHow...   
478QYNLw6dhTTx4oEkhBeq  Empty mansion, in the rain just off the coast\...   
3C4fzUgIP3ahkhOBdP38GM  MEDUZA & Goodboys - Piece Of Your Heart\nAvici...   
79zGYOcAe2VmJsyQiJX31a  I have to go, I'm so sorry, but it feels so co...   
6B2NRQjtSOtqi67d72r5cx  This a number one champion sound\nYeah, Estell...   
08rBIlTMXlF5uEHobZglxv  If it's gonna break me\nWon't you let me go?\n...   
1BmdqDrBU5eohtRwHBls6C  Lately, I've been reelin', watching the nightl...   
3kgKVcBpBGuSeaEC0AZGlb  Oh, oh-oh\nOh\n\nYeah, I'm gonna take my horse...   
3utdq3dPLVD4r7Vv9BnCAI  Ah-ooh\n\nI met her on a Monday evening\nShe w...   
1ppOGANOzMT01Cxh9jx4hN  Go (X22)\n\nThey say go, so I start slow\nBuil...   
6wKJjrWWP4qpzYbE8oQkc4  Somebody once told me the world is gonna roll ...   
6EDH26ppl7R8oV4tGilCkS  Dreams, dreams, dreams\n\nI've been havin' dre...   
1nwoWaqzB30bD4IPqRNuex  4/1\nAriana Grande & Victoria Monet - "MONOPOL...   
4fDBElPGDqZQ3rJorZTm2w  Sometimes don't wanna fall in love 'cause I'm ...   
6AZ21kPj2a0INgf3uCviVu  Hey\nBeautiful, beautiful, beautiful, beautifu...   
3uXHSf9sSIpOJWuC1H8DiU  Yeah, started off right\nI can see it in your ...   
4Q9iBGT9b9CVTtDwsgQWnl  If you want my future, forget my past\nIf you ...   
6B9cqNooxIyPfr3P5EB8LA  It's not what you said, it's how you said it\n...   

                                    gpt_ratings  
track_

The for loop to retrieve the ratings are working as it should and the scores do not seem suspicious. Great!

In [91]:
# fill these in for the nulls in the larger dataframe as well
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_subset_4['gpt_ratings'])
# let's check the larger dataframe, there should be 110 non-null gpt_ratings
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   110 non-null    object
dtypes: object(2)
memory usage: 470.4+ KB


Next, I get the ratings for the first 1000 lyrics.

In [92]:
df_subset_5 = df.head(1000) # create a subset dataframe from teh first 1000 rows in the larger dataframe
df_subset_5.info() # check the non-null counts, should be 100+ (does not need to be 110 since those 10 were random)

<class 'pandas.core.frame.DataFrame'>
Index: 1000 entries, 0r7CVbZTWZgbTCYdfa2P31 to 48qKqo6HgIG8VLN4CpYb37
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  1000 non-null   object
 1   gpt_ratings   101 non-null    object
dtypes: object(2)
memory usage: 23.4+ KB


In [93]:
df_subset_5.head() # let's check the first 5 rows (ratings will not be null, that's okay)

track_lyrics  \
track_id                                                                    
0r7CVbZTWZgbTCYdfa2P31  Here's to the ones that we got\nCheers to the ...   
1z1Hg7Vb0AhHDiEmnDE79l  Summertime and I'm caught in the feeling\nGett...   
75FpbthrwQmzHlBJLuGdC7  Two kids with their hearts on fire\nWho's gonn...   
1e8PAfcKUYoKkxPhrHqw4x  I'm going under and this time I fear there’s n...   
7fvUMiyapMsRRxr07cU8Ef  L.A. on a Saturday night in the summer\nSundow...   

                                    gpt_ratings  
track_id                                         
0r7CVbZTWZgbTCYdfa2P31  9 8 9 8 7 9 7 6 5 4 5 8  
1z1Hg7Vb0AhHDiEmnDE79l  8 6 8 7 5 8 4 6 5 4 5 7  
75FpbthrwQmzHlBJLuGdC7  9 8 9 8 7 9 8 6 5 4 5 8  
1e8PAfcKUYoKkxPhrHqw4x  9 8 9 8 7 9 3 5 2 2 3 9  
7fvUMiyapMsRRxr07cU8Ef  9 8 9 8 7 9 6 4 3 3 4 7

In [94]:
# use the same for loop and get_ratings function to get the ratings with API calls
for index, row in df_subset_5.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_subset_5.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 101 times 'not null' at first

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
Getting ratings for Stripped to the waist
We fall into the 
Getting ratings for Ah-ooh, ooh, ah-ooh


Getting ratings for Call on me in my darkest hour
Now when l
Getting ratings for I'm no longer brokenhearted
So glad I ca
Getting ratings for This is our last goodbye
Don't come and 
Getting ratings for I been feeling low for so long
That my h
Getting ratings for Take me to a different place
Together wh
Getting ratings for I've gone too many nights
Chasing the sh
Getting ratings for We the Best Music!
Another one!
DJ Khale
Getting ratings for Dum-dum-da-da-da-da, dum-dum-da-da-da
Du
Getting ratings for If I told you this was only gonna hurt
I
Getting ratings for You know what's coming, you caught the f
Getting ratings for (Hey)

僕以外 幸せそう なんだ
笑うのが 泣くよりも 辛いんだ
今 我慢
Getting ratings for Break, break
Break, break, break, break,
Getting ratings for またキミがボクを追い越していく
まるで時計の針さ 瞬間の rendezvous

Getting ratings for 誰だって強くないわ 胸が痛い ことだらけ But
誰だって弱くもないわ Wow 
Getting ratings for ​DAOKO「御伽の街」の歌詞

御伽の街に私落とし前つけにきました　これはマジ
Getting ratings for Look at me, heiki soudesho
You got me, n
Getting ratings for 闇を纏い

Getting ratings for You see that gyal there? Yeah, it's my o
Getting ratings for When you're dressin' up, still, it's not
Getting ratings for (Ghost, ghost, ghost, ghost)
(Ghost, gho
Getting ratings for DJ Khaled - Higher (feat. Nipsey Hussle 
Getting ratings for Ooh, hmm
Let's go

You look so good in a
Getting ratings for Made plans with me and all your friends

Getting ratings for Everything, everything's cool now
I want
Getting ratings for And the spirit of John moved upon the fa
Getting ratings for Do it again
Do it again
Do it again
Do i
Getting ratings for I'm sorry but, don't wanna talk
I need a
Getting ratings for Body to, ooh
Body to body

We should tak
Getting ratings for When I get too on ya
And I wanna call ya
Getting ratings for I be going in in the VIP with the finest
Getting ratings for Drake - One Dance feat. Kyla & WizKid
Mi
Getting ratings for We used to hide under the covers
Serenad
Getting ratings for Hello, sweet grief
I know you'll be the 
Getting ratings for We w

Getting ratings for Mmh (Luna-na, yeah)
Uh, na na (Luna-na, 
Getting ratings for Billie Eilish - everything i wanted
Khal
Getting ratings for Mmh, mmh, mmh

Yeah, ye-eah, ye-eah
Gyal
Getting ratings for Yatra, Yatra
Oh-uoh-uoh-uoh (Yeah-yeah, 
Getting ratings for Me hiciste preguntarme
Si era verdad mi 
Getting ratings for (This is the remix)
Mamarre, mamarre, ma
Getting ratings for Me conocen por culpa del aire
Me conocen
Getting ratings for Épico
Salte 'el medio, ¿okay?
Yeh-yeh-ye
Getting ratings for Sé que hay cosas que me digo
Que no tien
Getting ratings for Ladies and gentlemen, this is Mambo Numb
Getting ratings for Ayyayaya coco jambo ayyayai
Ayyayaya coc
Getting ratings for Yo, listen up, here's the story
About a 
Getting ratings for Hiya Barbie
Hi Ken!
Do you want to go 
Getting ratings for What is love?
Baby don't hurt me
Don't
Getting ratings for Ska-badabadabadoo-belidabbelydabbladabbl
Getting ratings for Sí señor, efectos especiales, yè, yè, yè
Getting ratings for La da da

Getting ratings for Higher than all, higher than any thought
Getting ratings for Yeah, yeah, I need You to fight for me
W
Getting ratings for You are the answer for a true revival
Ma
Getting ratings for I got my back to the sun ’cause the ligh
Getting ratings for Empty me of everything that's selfish
’C
Getting ratings for You are maker of all, You are made by no
Getting ratings for (I'm human)
(I'm human)

Take a second, 
Getting ratings for O-oh o-oh
Oh-oh-oh-ohh, ohh-oh
O-oh o-oh
Getting ratings for Though I walk through the valley
Or a se
Getting ratings for Where would I be?

I’m not afraid, You’r
Getting ratings for Well, I thought that I had seen most eve
Getting ratings for I missed a thousand moments
I traded pre
Getting ratings for Just as I am, without one plea
But that 
Getting ratings for Yeah, shout to everybody
Who's been on t
Getting ratings for Covenant maker, I made a start
Covenant 
Getting ratings for JANUARY

Tha God Fahim - Tha Dark Shogun
Getting ratings for This

Getting ratings for Viceroy
Early in the morning
Just trying
Getting ratings for Don't touch my hair
When it's the feelin
Getting ratings for I was raised up believing I was somehow 
Getting ratings for A new world hangs
Outside the window
Bea
Getting ratings for I could bet all the riches that I ever h
Getting ratings for Stand up straight at the foot of your lo
Getting ratings for Pristine
Untraced by the world outside y
Getting ratings for Girl
If they don't know your worth
Tell 
Getting ratings for It feels like I only go backwards, baby

Getting ratings for Now that you're gone, it's been a long, 
Getting ratings for I was walking through icy streams
That t
Getting ratings for I don't wanna be funny anymore
I don't w
Getting ratings for Taking it slow, saving up, she
Before sh
Getting ratings for ...It's just not right, it's

I don't wa
Getting ratings for Make it rain, girl, make it rain
Make it
Getting ratings for Friends are warmer than gold when you're
Getting ratings for Yeah

Getting ratings for If you don't wanna see me

Did a full on
Getting ratings for I got room in my fumes (Yeah)
She fill m
Getting ratings for Fuck you, and you, and you
I hate your f
Getting ratings for Father, I stretch
Stretch my hands to Yo
Getting ratings for Travis Scott - HIGHEST IN THE ROOM
Camil
Getting ratings for Yeah

They fell in love one summer
A lit
Getting ratings for I'm done hatin' myself for feelin'
I'm d
Getting ratings for What do you mean?
I'm sorry by the way
N
Getting ratings for DaBaby - BOP
French Montana - Writing on
Getting ratings for Did I really just forget that melody?
Na
Getting ratings for Hər şey alovlanır, sevirəm istini
Coşdur
Getting ratings for Selena Gomez - Lose You To Love Me
Selen
Getting ratings for It's crazy when
The thing you love the m
Getting ratings for Se acostó temprano, mañana hay que estud
Getting ratings for Dua Lipa - Don't Start Now
Ariana Grande
Getting ratings for (Yeah)
¡Gangalee! (Uh-uh-uh)
Ra-Rauw

¿C
Getting ratings for No, 

In [95]:
df_subset_5.info() # check that there are 1000 non-null values in the gpt_ratings column

<class 'pandas.core.frame.DataFrame'>
Index: 1000 entries, 0r7CVbZTWZgbTCYdfa2P31 to 48qKqo6HgIG8VLN4CpYb37
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  1000 non-null   object
 1   gpt_ratings   1000 non-null   object
dtypes: object(2)
memory usage: 55.7+ KB


In [100]:
df_subset_5.tail(20) # check the last 20 scores to see if anything looks strange

track_lyrics  \
track_id                                                                    
4cZ3UsiKd1kUQIaq4BFIj2  Thoughts of you and me keep passing by\nLike s...   
04ZTP5KsCypmtCmQg5tH9R  Everything's been so messed up here lately\nPr...   
3K01q0jtSNHeqx5gs97HH2  Yeah\nCome on now\nHere we go\nLet's do it\nYe...   
6RjW45KHJ6kgI2xQ1aFa52  Used to be your baby, used to be your lady\nTh...   
7pAq1IXYZpL42HchCminu6  Don't hold your breath\n\nYou can't touch me n...   
2GJEMlKxt3GL2rJMOTET6Z  You just keep tuggin', pushin', pullin'\nOn my...   
6lanRgr6wXibZr8KgzXxBl  Heart beats fast, colors and promises\nHow to ...   
3KnjerEPMolLapVo2wdgz6  Saturday, steppin' into the club\nSomebody wan...   
44aN5xKL3kGHvQ5bXVk6B8  Died last night in my dreams\nWalking the stre...   
65YX6qx31L6SOQlrSMGYeM  I want someone to love me\nFor who I am\nI wan...   
2v00WuRHH1WdnXxlHnyURi  I crashed my car the other day\nToo busy think...   
0X5p2uVpPIbHIMzyH7ky3V  Every clock is tickin' faster\nTakin' trips ar...   
61e03HSUanPGL3M3WSiJgE  I've been trying to let it go\nBut these butte...   
5FNS5Vj69AhRGJWjhrAd01  If you stay for this minute\nGirl, I'll never ...   
24aMOBYVHE58Y33RIwkT0L  The way you're looking at me like I don't alre...   
1rM0CnyUiiw6A9CHJRXjZA  Let me tell you something you can really trust...   
3TcL0dyCMyr0kyTTc4NLgI  I wouldn't wanna be anybody else\nHey\n\nYou m...   
1UXBbmjIrxjckrbv5EfSVT  Tell me something I don't know\n\nEverybody te...   
0hnHoQbEQOL4YUZ4SO6xbe  Calling all the monsters, calling all the mons...   
48qKqo6HgIG8VLN4CpYb37  Oh, oh, oh, it's magic, you know\nNever believ...   

                                    gpt_ratings  
track_id                                         
4cZ3UsiKd1kUQIaq4BFIj2  9 8 9 8 7 9 4 4 3 3 3 7  
04ZTP5KsCypmtCmQg5tH9R  9 8 9 8 7 9 7 6 5 4 6 8  
3K01q0jtSNHeqx5gs97HH2  9 6 9 8 5 9 7 6 5 4 4 5  
6RjW45KHJ6kgI2xQ1aFa52  9 8 9 8 7 9 6 5 4 3 4 8  
7pAq1IXYZpL42HchCminu6  8 6 8 7 6 8 3 2 9 9 8 6  
2GJEMlKxt3GL2rJMOTET6Z  9 8 9 8 7 9 7 6 5 4 6 8  
6lanRgr6wXibZr8KgzXxBl  9 9 9 8 8 9 8 7 3 3 3 8  
3KnjerEPMolLapVo2wdgz6  8 7 8 7 6 8 6 6 4 4 5 7  
44aN5xKL3kGHvQ5bXVk6B8  9 8 9 9 8 9 3 6 4 4 4 8  
65YX6qx31L6SOQlrSMGYeM  8 8 8 8 7 8 5 5 4 4 6 7  
2v00WuRHH1WdnXxlHnyURi  9 8 9 8 7 9 4 5 7 4 5 9  
0X5p2uVpPIbHIMzyH7ky3V  9 8 9 8 7 9 8 7 6 4 5 8  
61e03HSUanPGL3M3WSiJgE  8 6 8 7 6 8 7 6 5 4 4 6  
5FNS5Vj69AhRGJWjhrAd01  9 6 9 8 7 9 8 6 5 4 5 7  
24aMOBYVHE58Y33RIwkT0L  8 7 8 7 6 8 4 4 5 4 4 7  
1rM0CnyUiiw6A9CHJRXjZA  9 6 9 8 7 9 4 4 6 4 6 7  
3TcL0dyCMyr0kyTTc4NLgI  9 8 9 8 7 9 8 6 3 3 4 8  
1UXBbmjIrxjckrbv5EfSVT  9 8 9 8 7 9 6 5 4 4 5 8  
0hnHoQbEQOL4YUZ4SO6xbe  9 6 9 8 7 8 4 4 3 3 4 5  
48qKqo6HgIG8VLN4CpYb37  9 8 9 8 7 9 8 7 5 5 6 8

The scores look okay. Let's fill the nulls in the larger dataset with these.

In [101]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_subset_5['gpt_ratings']) # fill in the nulls
df.info() # check that there are over 1000 non-nulls 

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   1009 non-null   object
dtypes: object(2)
memory usage: 470.4+ KB


In [102]:
df_subset_5.to_csv('first_thousand_ratings.csv') # let's write this dataframe to a csv as a backup

In [104]:
df_subset_6 = df.head(5000) # create a subset with the first 5000 lyrics from the larger dataset
df_subset_6.info() # check that there are over 1000 non-null values in gpt_ratings

<class 'pandas.core.frame.DataFrame'>
Index: 5000 entries, 0r7CVbZTWZgbTCYdfa2P31 to 358uP4VwX0XYKji2IW19zi
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  5000 non-null   object
 1   gpt_ratings   1002 non-null   object
dtypes: object(2)
memory usage: 117.2+ KB


In [105]:
# use the same for loop and get_ratings function to make API calls to get the ratings
for index, row in df_subset_6.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_subset_6.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print ~1000 'not null' at first

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

Getting ratings for All the girls on the block knocking at m
Getting ratings for Austin M, keep doing your thing
Let thes
Getting ratings for Se oye una canción que hace suspirar
Y h
Getting ratings for Tantos días sola en mi ventana
Tantos añ
Getting ratings for Ya son las siete, hay que ponerse en mar
Getting ratings for Para conseguir lo que quieres, debes con
Getting ratings for Brilla, linda flor
Dame tu poder
Vuelve 
Getting ratings for Se oye una canción que hace suspirar
Y h
Getting ratings for He buscado siempre aquí una respuesta
Es
Getting ratings for Yo, yo, yo
Yo, yo, yo
Yo, yo, yo
Mmm, ay
Getting ratings for We can’t, we can’t back down

We can’t, 
Getting ratings for It's like, he doesn't hear a word I say

Getting ratings for So let's sing na, na na na na, hey ya
Cm
Getting ratings for 'Cause we rock
We rock, we rock on
We ro
Getting ratings for Every time I think I'm closer to the hea
Getting ratings for I've always been the kind of girl that h
Getting ratings for They

Getting ratings for Ruined again, what did I do?
I've been 
Getting ratings for We had a bad day, nothing to say on the 
Getting ratings for She had the '59 out
Daddy let her drive 
Getting ratings for He sees them both everyday now
He watche
Getting ratings for I figured I’d go at the least to check i
Getting ratings for I'm not a hopeless romantic
I'm just rom
Getting ratings for Picture this
The rain is point outside
A
Getting ratings for The lights begin to dim and I've been
A 
Getting ratings for Girl, you remind me of summertime
But no
Getting ratings for You move through my body like an ocean
D
Getting ratings for (Yeah, that's cool
So it's gonna have to
Getting ratings for Everyone wants to call it all around our
Getting ratings for I miss you, miss you

Hello there 
Th
Getting ratings for The drops of rain they fall all over
Thi
Getting ratings for In the car I just can't wait
To pick yo
Getting ratings for Push it out, fake a smile
Avert disaste
Getting ratings for It's hard 

Getting ratings for Back in black, I hit the sack
I've been 
Getting ratings for As I walk through the valley of the shad
Getting ratings for Ooh-ooh, wow
Ahh, yeah-yeah (Wow)
Yeah-y
Getting ratings for Lately I've been dreaming of a life
Told
Getting ratings for Tell me I'm your only when you look me i
Getting ratings for Forecasters say more bad weather
But the
Getting ratings for Eyes meet across the floor
Your name, I 
Getting ratings for There will be blood, run for your life
G
Getting ratings for I wish that you and I lived in The Sims

Getting ratings for Go to work
Treat my body like a 9 to 5
I
Getting ratings for Uncharted, unfaded
No questioning what w
Getting ratings for Look at what you started
Now you can't b
Getting ratings for Tell me all your sweet, sweet little lie
Getting ratings for I remember the rush
We were running, bac
Getting ratings for All the little gifts you gave
I call it 
Getting ratings for She told me that she loved me by the wat
Getting ratings for I’m 

Getting ratings for If you wanna say something, say it now
C
Getting ratings for Hey, what's the big idea?

Yo Mika.

I s
Getting ratings for Do I attract you?
Do I repulse you with 
Getting ratings for Fresh kid Z, fresh kid C (Yes, sir)
Fres
Getting ratings for Adventure of a Lifetime Lyrics Turn your
Getting ratings for And said drink from me, drink from me
(I
Getting ratings for Translations Türkçe Português Français Ε
Getting ratings for Pour up (Drank), head shot (Drank)
Sit d
Getting ratings for Yeah, yeah, yeah, yeah
Thought you was c
Getting ratings for Oh my
Oh my

Fuck the law, they can eat 
Getting ratings for Motherfucker

Vroeger was ik nooit lief

Getting ratings for Ik vouw papier, kom niet zeggen dat jij 
Getting ratings for I got a bone to pick
I don't want you mo
Getting ratings for Dance (Hu hu hu hu hu)
(Hu hu hu hu hu)

Getting ratings for I've been thinking about the way you loo
Getting ratings for Off with your head
Dance 'til you're dea
Getting ratings for Tran

...

Getting ratings for Escribo por religión aunque la inspiraci
Getting ratings for Hispana, Zimple, DJ Mush K, DJ Phat
Repr
Getting ratings for Déjame entrar, quiero estar contigo (Ah)
Getting ratings for Tengo un problema
Esperarte es un dilema
Getting ratings for Todo va a estar bien, todo va a estar bi
Getting ratings for Corre, vive, siente, canta
Martes Trece 
Getting ratings for Pa' mis homies
Pa' las ladies
Pa' mi gen
Getting ratings for Abre las mentes que puedas con la llave 
Getting ratings for No te quiero perder
Que la distancia se 
Getting ratings for Wait two secs, let me spark this zoot
My
Getting ratings for Motherfucker, move back

Motherfucker, m
Getting ratings for All the second stage tanks now pressuriz
Getting ratings for Vaya loco, ¿no somos todos iguales?
Comi
Getting ratings for Te voy a volver tan loca
Cuando te bese 
Getting ratings for Hey hey hey no se lo creen
Llegan los ni
Getting ratings for Oh, vuela el aroma de mi piel sobre tu p
Getting ratings for No m

Getting ratings for Forced to battle in life, or rather in d
Getting ratings for California love

California, knows how t
Getting ratings for Angels, comin' from all angles
Better wa
Getting ratings for Yeah.. I wanna take this time to dedicat
Getting ratings for It's kind of easy when you listen to the
Getting ratings for Lemme tell you sumnn
Kepler seven, seven
Getting ratings for 4x
Awww yeah! Do you wanna ride wit us?

Getting ratings for Fuck Black hippy nigga, I invented the r
Getting ratings for These, these, these niggas lame as hell

Getting ratings for California sunshine
California sunshine

Getting ratings for That's the alkaholiks functions, conjunc
Getting ratings for Double up
Three or four times, I ain't t
Getting ratings for May I have your attention please
The fol
Getting ratings for Let me take you on a Quasimoto rhyme rid
Getting ratings for Yo, we are no superstars
Who want to be
Getting ratings for (Welcome to L.A)
Where you can see the w
Getting ratings for Yo ma

Getting ratings for These hacks don't live by the code
The s
Getting ratings for PA, PA, and I keep yelling it
But y'all 
Getting ratings for Where the hoes, where the hoes
Lookin',
Getting ratings for Whaaat
Smoke somethin', bitch...smoke so
Getting ratings for (Cormega)
Yo, laid back like a fat buddh
Getting ratings for Hallelujah can tell this 
Devin's got s
Getting ratings for (Devin) Walk up in da session wit my dic
Getting ratings for featuring Scarface 



Scarface Intr
Getting ratings for Do you ever see that stuff that be
When 
Getting ratings for My old boy from the point
But I'm from S
Getting ratings for Let me get a chop at this lumber
Niggas 
Getting ratings for Put your stones in dust and worn, South 
Getting ratings for Peep that, feel this, I'm in here with m
Getting ratings for This is for the Bourbons and the Cadilla
Getting ratings for Ghetto dreams baby
That's what we talkin
Getting ratings for Unngghh, How you do that there (Remix), 
Getting ratings for This is fo

Getting ratings for Instrumental: F*ck Up Some Commas by Fut
Getting ratings for Wassup Pablo? What's poppin?
You got th
Getting ratings for I'm in my penthouse half-naked
I cooked 
Getting ratings for Ayy, gang, gang, nigga
Gang, gang, nigga
Getting ratings for My hunger is equal to my struggle
I came
Getting ratings for Ooh-ah, ooh-ah, ooh-ah
Ooh-ah, I keep me
Getting ratings for Peep the story
Sonny Cheeba, Geechi Sued
Getting ratings for I can see that bullshit from a mile away
Getting ratings for Its a lot of violence around here
So a l
Getting ratings for Young Chop on the beat
Fft, beep, beep, 
Getting ratings for Rainstorm the back of the bank, bustin l
Getting ratings for Yo, the saga begins, begin war
I draw fi
Getting ratings for That ain't a home
It's a furnace in need
Getting ratings for Yo, shout out to everybody that worked o
Getting ratings for Steady ride with my niggas, I be slidin'
Getting ratings for We gotta
We gotta
We gotta
We gotta kick
Getting ratings for For m

Getting ratings for You fuckin' thieves
We D4L
And we back, 
Getting ratings for Zaytoven (Oh)
Super
You can feel the pai
Getting ratings for Hahaha
Yeah!
Ahh Yee-uhh, Boii Ah Yee-uh
Getting ratings for There's gon' be some stuff you gon' see

Getting ratings for BandPlay
Yeah, yeah, yeah, yeah, yeah
Ye
Getting ratings for Huh
Yea baby girl, you know how it's goi
Getting ratings for Yeah

These niggas, they lame
223 bullet
Getting ratings for House real big
Cars real big
Belly rea
Getting ratings for Katy Perry - Harleys In Hawaii
BTS - Mak
Getting ratings for You know who this is mayne
Big Kuntry Ki
Getting ratings for That girl ooh, that girl ooh, that girl,
Getting ratings for You say you a hit man but you ain't hit 
Getting ratings for I been poppin (I'm not myself)
I been dr
Getting ratings for Aha, I'm so fresh man (Eardrummers, eard
Getting ratings for It's the blackout, 'Rari got the back ou
Getting ratings for Teen drinking is very bad
Yo I got a fak
Getting ratings for ChaseT

In [106]:
df_subset_6.info() # check that there are 5000 non-null values in the gpt_ratings column

<class 'pandas.core.frame.DataFrame'>
Index: 5000 entries, 0r7CVbZTWZgbTCYdfa2P31 to 358uP4VwX0XYKji2IW19zi
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  5000 non-null   object
 1   gpt_ratings   5000 non-null   object
dtypes: object(2)
memory usage: 246.2+ KB


In [107]:
df_subset_6.tail(20) # check the last 20 scores to detect anything strange, they seem okay

track_lyrics  \
track_id                                                                    
7yqzwyCbAsGYNdVWQTLZoL  Yeah\nYou know me and and Riff Raff ain't abou...   
0yEYKmKPG8ktvYJ753J3jg  I′m T.K. Soul\nI'm lookin’ for a lady\nSaid, I...   
5ahbge6cAozopYL2EeJg82  Once upon a time\nWe were a unit, we were a pa...   
5ze2tIC1kKvaFFf0nP9iNR  Ooh, ooh ooh\n\nMy baby and are back together ...   
27KUSXaBq6gpAGq2edLemr  Yeah, and when this shit drop\nDon't be callin...   
1xJrQgMoWUiRvZyl1KCXYW  Got a brand new song, yo\nA little somethin' f...   
2a4vn9kHPnBUBGWPnhHRav  Well, well\nSay it now, baby, mhmm\nThey call ...   
22bnRpREhpBzy62K4QvdLX  I hear she’s been seeing\nThis loser since we’...   
0dVQeXMrjnNUqQOTQscgKe  Ooh\n\nAll of you ladies out there, turn up yo...   
2cvfU0e5s4fLlSjiCuQwFv  Just one lifetime\nOf loving you, honey\nWon't...   
5ol5vmBHvjrdEXfky3gsQk  I feel sorry, I feel sorry\r\nI feel sorry, I ...   
0zyyaMpWRZNSx2GqAMFKX3  Ah, she didn't bat an eye\nAs I packed my bags...   
1130yH9cDY39Onu6HDYFYP  I said tonight I'm getting throwed\nThat's rig...   
5EJZKffdlqfITcIce4oTM1  Hey, William, whats’ goin’ on?\nNot much, Jeff...   
2LNLenFZvgHlU6wKTQavij  Solid young nigga but they hate me\nGotta stay...   
2psbaFILwv134sGvLmziyJ  When I'm in the mood, my old man is not\nI tos...   
4vrOAcjaNkGkV2ZswUZHC1  Hello, may I speak to Barbara\nBarbara, this i...   
6HZILIRieu8S0iqY8kIKhj  I got, I got, I got, I got—\nLoyalty, got roya...   
7floNISpH8VF4z4459Qo18  Aye\r\nI'm like bitch, who is your mans?, aye\...   
358uP4VwX0XYKji2IW19zi  Yeah\r\nSex game had her ass blowing me up (br...   

                                    gpt_ratings  
track_id                                         
7yqzwyCbAsGYNdVWQTLZoL  6 3 7 8 5 8 4 3 2 2 3 3  
0yEYKmKPG8ktvYJ753J3jg  8 6 8 7 5 8 6 5 4 4 5 6  
5ahbge6cAozopYL2EeJg82  8 8 8 9 8 8 4 3 4 5 6 6  
5ze2tIC1kKvaFFf0nP9iNR  7 8 8 7 6 8 4 4 3 3 3 6  
27KUSXaBq6gpAGq2edLemr  5 3 6 6 4 6 2 1 2 1 2 3  
1xJrQgMoWUiRvZyl1KCXYW  8 6 8 7 5 8 7 7 6 4 5 6  
2a4vn9kHPnBUBGWPnhHRav  8 6 8 7 6 8 6 5 4 4 5 6  
22bnRpREhpBzy62K4QvdLX  7 6 7 6 5 7 4 4 3 3 4 6  
0dVQeXMrjnNUqQOTQscgKe  8 7 8 8 7 8 3 3 2 2 3 4  
2cvfU0e5s4fLlSjiCuQwFv  8 8 9 8 7 8 7 5 4 3 4 8  
5ol5vmBHvjrdEXfky3gsQk  9 8 9 8 7 9 6 3 3 3 4 8  
0zyyaMpWRZNSx2GqAMFKX3  8 7 8 7 6 8 4 4 4 4 4 7  
1130yH9cDY39Onu6HDYFYP  6 4 7 5 3 7 4 4 5 6 4 6  
5EJZKffdlqfITcIce4oTM1  7 6 8 7 5 7 4 4 6 4 5 7  
2LNLenFZvgHlU6wKTQavij  6 3 5 6 5 6 2 1 8 8 7 8  
2psbaFILwv134sGvLmziyJ  7 6 8 7 5 8 4 3 6 2 3 5  
4vrOAcjaNkGkV2ZswUZHC1  9 8 9 8 7 9 3 2 5 6 4 8  
6HZILIRieu8S0iqY8kIKhj  7 8 9 8 7 9 3 2 8 6 5 7  
7floNISpH8VF4z4459Qo18  6 3 7 5 2 7 2 1 1 1 1 1  
358uP4VwX0XYKji2IW19zi  6 5 8 7 6 8 4 3 2 3 4 5

In [108]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_subset_6['gpt_ratings']) # fill the nulls in the larger dataset
df.info() # check that there are now over 5000 non-null gpt_ratings in the larger dataset

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   5007 non-null   object
dtypes: object(2)
memory usage: 470.4+ KB


In [109]:
df_subset_6.to_csv('first_five_thousand_ratings.csv') # write this dataframe to a csv for backup

Now I finally try this process with the whole dataframe (~20k rows).

In [110]:
# use the same for loop and function to retrieve gpt_ratings
for index, row in df.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should pring a lot of 'not null's at the beginning

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

Getting ratings for Every time I pull up at the let out it's
Getting ratings for Yeah, King Push
I could tell you what th
Getting ratings for I'ma do this one for my homies gone
The 
Getting ratings for Yeah, and it got a soul, yeah
Uh-uh, wha
Getting ratings for We 'bout to pull up (sheesh!)
Who you pu
Getting ratings for Make it, make it, make it, boy, we gotta
Getting ratings for Show me the booty
Show me the baggage
Sh
Getting ratings for Super!
They go crazy, yeah
They comin' i
Getting ratings for Oh, no, no, no, no
No, no, no, no
No, no
Getting ratings for And the next door neighbours are all so 
Getting ratings for (Helluva made this beat, baby)

These ni
Getting ratings for Soulja
2 gunz up in the air (Soulja)
Who
Getting ratings for Slatt!
Ayy, get out your motherfuckin' s
Getting ratings for I cut the small talk, I just need all ca
Getting ratings for Uhh, alright
I did, haha, yeah

Used to 
Getting ratings for Thank God I got it, thank God I got it
T
Getting ratings for Uh-h

Getting ratings for Mystery repeats
Life got tricks but it t
Getting ratings for I roll up
I roll up
I roll up
Shawty I r
Getting ratings for What? Yeah
Woo, woo, woo
Woo, what?
Uno,
Getting ratings for Mijn schatje is lady-like
Ze heeft klein
Getting ratings for Mmmm, ay-oh
Hey...
Ratatat, yeah!
Na-na-
Getting ratings for Uh-uh, uh-uh
One, two, one, two, one, tw
Getting ratings for Stuttering
Give 'em the rest and make 'e
Getting ratings for Human beings in a mob
What's a mob to a 
Getting ratings for Work hard, play hard
Work hard, play har
Getting ratings for Another night, slips away
In other words
Getting ratings for I don't know what you heard about me
But
Getting ratings for It's the Infamous Mobb, M-O-B-B (Ha, ha)
Getting ratings for Gee willikers, Gatman, they got me surro
Getting ratings for Okay, okay, okay (Okay, okay, okay)
Okay
Getting ratings for Ik ben fucking gelukkig, 'k heb alles op
Getting ratings for Laat me je Lien zien Lienie

Handen in d
Getting ratings for Big 

Getting ratings for Paw paw paw paw
Afro Trap partie 4
Fais 
Getting ratings for Yeah ayy!
Yeah ayy!
Yeah Boyz
Yeah
Hol' 
Getting ratings for Dites-moi d'où il vient
Enfin je saurai 
Getting ratings for Do I got time for this money (Yeah)
Do I
Getting ratings for Nothing can stop me, I'm all the way up
Getting ratings for Painting pictures from a city they forgo
Getting ratings for Mobb Deep - "Shook Ones, Pt. II"
Dionne 
Getting ratings for This is the activation of the emergency 
Getting ratings for First let me hop out motherfucking Porsc
Getting ratings for I know you've been goin' through some th
Getting ratings for Came in at first, had bad luck
Got a who
Getting ratings for Young Mula, baby!
(Let me see)
Haha
You 
Getting ratings for Alright girls, get up and let's get this
Getting ratings for She a bad bitch
Ain't worryin' 'bout not
Getting ratings for You, you my only one
You my number one
Y
Getting ratings for Tell me what your body wanna know
Fly yo
Getting ratings for Walk 

...

Getting ratings for This is my rebel yell

What about freedo
Getting ratings for I want you to stay but I tell you to go

Getting ratings for Woke up, feeling overtired
Been working 
Getting ratings for She's building me up
And she's tearing m
Getting ratings for Best in the game, that's all facts (Yeah
Getting ratings for All of a sudden they see that I'm making
Getting ratings for Oh yeah, yeah, yeah
Oh yeah, yeah, yeah

Getting ratings for I wanna grow old with you, buy an RV and
Getting ratings for I feel like dancein' in the moon light
R
Getting ratings for When the old soles have shoes are worn t
Getting ratings for Lately I'm, lately I'm
Racing through ti
Getting ratings for You can't stop it
You can make it yeah
Y
Getting ratings for Heart is racing, things are changing
You
Getting ratings for Sorry that I love you
I know that’s not 
Getting ratings for Let me live on the line
I got a little f
Getting ratings for Show yourself
There's nobody else
Stri
Getting ratings for I see 

Getting ratings for Si un niño se pierde...
Y en la madad de
Getting ratings for Andate con el alto y dejame acá
Que debe
Getting ratings for Gente aburrida que busca tranquilidad
Os
Getting ratings for Siento que tu respiración
Es el oxígeno 
Getting ratings for Barras de luz entran por mi ventana
Mezc
Getting ratings for Todo lo que viene yo lo pido
En cada mom
Getting ratings for Mis huellas dibujadas en el barro
Esquiv
Getting ratings for Wakan Tanka
Gran espíritu
Agradeco
Pacha
Getting ratings for Mhm, no sleep

We open wide, these eyes 
Getting ratings for Es, lo que yo siento adentro
Es, un fueg
Getting ratings for Prima de mi corteza
Duda morena que me t
Getting ratings for La pue-, la puer-
La puerta esta entreab
Getting ratings for Brilha
Estrada, coração, farol de milha

Getting ratings for Hoy no me quiero preocupar
De las deudas
Getting ratings for Tu nombre traigo este día
Para darme fel
Getting ratings for Soñaba con ser un rockstar
Pero todo cam
Getting ratings for D-D-

Getting ratings for Ya basta
De hacer conmigo todo lo que qu
Getting ratings for ANTHONY: Oh My God!
HENRY: Te pronuncias
Getting ratings for He came to the rescue of nothing in 1916
Getting ratings for Estoy brillando con highlighter, ¿no lo 
Getting ratings for Guallando!
Y ahora e' que la cosa se va 
Getting ratings for Now hear this (Now hear this)
Ah, rodeo

Getting ratings for Oye, mamá, tú sí estás buena en verdad
T
Getting ratings for (Yeh, yeh, yeh)

Pásame la hookah, ¡eh!

Getting ratings for Aquel día te vi y tu energía sentí
Desde
Getting ratings for Letra de "Dándole (Remix)" ft. Jowell & 
Getting ratings for Minha navalha carrega o fio da vida
Minh
Getting ratings for Eu determino que termine aqui e agora
Eu
Getting ratings for Que coragem você tem de me ligar
Às quat
Getting ratings for Eu só queria entender
Por que é que você
Getting ratings for Apaga a luz e deixa o tempo passar
Baby,
Getting ratings for Fechando o som, ei

Sandália de couro, d
Getting ratings for Pela

Getting ratings for Un olor a tabaco y Chanel
Me recuerda a 
Getting ratings for Sabe que no me parezco a nadie
Ahora tod
Getting ratings for Woh-oh-oh-oh
Woh-oh-oh-oh

Quiero que me
Getting ratings for 24 horas ya no son suficientes para amar
Getting ratings for Ehi, ehi, è inutile che continuate a far
Getting ratings for Miento cuando niego que te quiero
Pero v
Getting ratings for Da l' bi smeo sve da pukneš i da probaš 
Getting ratings for Soy yo quien te ama
No, no lo dudes por 
Getting ratings for Genres | GênerosI listened to 42 genres 
Getting ratings for Letra de "Roast Yourself"
Sin justificac
Getting ratings for DJ Buxxi
Juan Magán
Electro latino

Y yo
Getting ratings for Letra de "El Challet (Remix)" ft. Lary O
Getting ratings for Jay Kalyl, ouh-no-no
Yo sé que cuando es
Getting ratings for Eu sempre fui daquele tipo mais relax
De
Getting ratings for Shit

This time's low, pero no tan fresh
Getting ratings for Tranquilo, chango, que estoy a tu lado
A
Getting ratings for Mery

KeyboardInterrupt: 

I stopped the kernel to see how many have been saved so far after some time.

In [111]:
df.info() # it seems like half the ratings have been retrieved so far

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   10604 non-null  object
dtypes: object(2)
memory usage: 986.5+ KB


In [112]:
df.to_csv('first_ten_thousand.csv') # save this dataframe to a csv as backup

In [114]:
df[:10604].tail(20) # let's see where I stopped the kernel

track_lyrics  \
track_id                                                                    
4lhe5Iy0XVRoySNQYMvP1l  It is such a good night to kiss\nIt is such a ...   
55hgAzy1kaC0Cn7EFxDeUz  How does one become a successful person?\nGet ...   
5sm8mtcQQOhKT8YgCBwVNr  Yeah, we going all around the world\nYou know\...   
1Ksf0moFKGhOJ6uNgQcEAT  “It’s too bad the Ghost has lost her masts.  W...   
6ADPydLM8fmi6fjO9ZXAb8  This is so stupid i'm just talking to y'all th...   
0Cevaujuf5Os3lb5KrV0IH  You ain't gotta front\nAlready know your strat...   
6L778PA16SuyYvFhqnMndY  I'm a motherfuckin' starboy\n\nI'm tryna put y...   
5sWevAyvYSRzGpIsdsRvJi  Fighting flames with fire\nHang onto burning w...   
7aV2mflaASUmGhCErm7kBO  Nevada!\r\nMark Morrison!\r\n\r\nWell, I tried...   
2sTe3y5xjQvVb9tDTVaI35  Wisdom, like water, runs down to my feet\nThe ...   
2FfyiTnl5OPa1hYdCWZGdG  Can you tell me who to follow?\nWhen there's n...   
5hz9DEkahyWoTs3rxJOTtw  Words, I can hear the whispers about me\nAroun...   
3qaYuV5XZAwiOvGE91HhwS  Songs with a ✅ contain verified annotations an...   
0nPj7f507HUBm8BCBbv8on  Let's wait a while, we had a moment\nI spoke t...   
2FfH72VskV7KXasFtOWJs7  I ain't working (no)\nI ain't working all nigh...   
1gEK5unpcVyBc90uJRBtY6  When the leaves turn brown\nI watched it burn\...   
5eT5eYhcRfx9cjiflxZh8o  Your love, love your love\nYour love, love you...   
2ClIt2OnPCV2gV3dZQxyBz  Let's go\nYou may not see the consequences of ...   
6v9sCNj1KY3wblGJAohxX2  Lifetime waiting, getting busy with the number...   
4nYKI0JqkWfr1YbmH4ADEM  I thought I was a dreamer\nBut it's not a drea...   

                                    gpt_ratings  
track_id                                         
4lhe5Iy0XVRoySNQYMvP1l  9 5 8 6 3 8 9 3 3 3 3 3  
55hgAzy1kaC0Cn7EFxDeUz  8 9 9 8 7 9 3 2 8 9 8 9  
5sm8mtcQQOhKT8YgCBwVNr  6 5 8 8 7 7 3 3 4 4 4 5  
1Ksf0moFKGhOJ6uNgQcEAT  7 8 8 8 7 8 5 4 3 6 4 7  
6ADPydLM8fmi6fjO9ZXAb8  6 4 7 7 5 7 3 2 8 8 8 5  
0Cevaujuf5Os3lb5KrV0IH  7 6 7 6 5 7 6 6 5 4 5 6  
6L778PA16SuyYvFhqnMndY  6 3 8 6 4 8 3 2 1 1 2 3  
5sWevAyvYSRzGpIsdsRvJi  9 8 9 8 7 9 6 6 3 3 4 8  
7aV2mflaASUmGhCErm7kBO  8 6 8 7 6 8 4 4 6 4 4 6  
2sTe3y5xjQvVb9tDTVaI35  9 8 9 9 8 9 7 8 6 6 7 8  
2FfyiTnl5OPa1hYdCWZGdG  8 7 8 7 6 8 6 6 4 4 5 7  
5hz9DEkahyWoTs3rxJOTtw  9 7 9 8 7 8 6 6 5 5 4 6  
3qaYuV5XZAwiOvGE91HhwS  6 5 6 5 4 6 4 4 3 3 4 6  
0nPj7f507HUBm8BCBbv8on  8 6 8 7 6 8 7 6 5 5 5 6  
2FfH72VskV7KXasFtOWJs7  7 5 6 6 5 7 3 3 7 4 4 5  
1gEK5unpcVyBc90uJRBtY6  9 8 9 8 7 8 7 6 5 4 4 5  
5eT5eYhcRfx9cjiflxZh8o                      NaN  
2ClIt2OnPCV2gV3dZQxyBz                      NaN  
6v9sCNj1KY3wblGJAohxX2                      NaN  
4nYKI0JqkWfr1YbmH4ADEM                      NaN

In [121]:
df[10600:].head(20) # the null values start at the index 10600

track_lyrics  \
track_id                                                                    
5eT5eYhcRfx9cjiflxZh8o  Your love, love your love\nYour love, love you...   
2ClIt2OnPCV2gV3dZQxyBz  Let's go\nYou may not see the consequences of ...   
6v9sCNj1KY3wblGJAohxX2  Lifetime waiting, getting busy with the number...   
4nYKI0JqkWfr1YbmH4ADEM  I thought I was a dreamer\nBut it's not a drea...   
7uJz1nHWR8TScmdnEhI8p4  Feel the chills run down your spine\nDown to y...   
1YXq6U6yY6aQ5dkndki7KC  No, my mind ain't right\nCold, so cold last ni...   
1w5sLDYzYAGI0AkLc6FPlO  I wanna love ya\nI wanna love you\nAnd treat y...   
6ksRossV4vKsXntCCZbhaM  Heartbreaks and promises\nI've had more than m...   
5uZlU3v9fq5ILATfqHvVwK  What would you do\nTo get to me\nWhat would yo...   
3NBDgwEAGMj0aKRsU8zoO9  We're like rivers in the night\r\nI go left an...   
1J2EmhjTmHQxLShYQK7Xti  Let's dance in style, let's dance for a while\...   
5WeryDMDd3BtnIIPthC7Gz  ( Mastar Vk )\nBuda ju nimeomoka nikipita kwa ...   
30cW9fD87IgbYFl8o0lUze  Always running on the move\nAin't a thing we c...   
4zLSkwZaiMfzzapPCbdG90  And I'm watchin' the late show\nIn my flat all...   
1Xq4fBayQtSJlcYZsPDY4C  Get up on the floor\nDancing all night long\nG...   
1Df5NAhInalMVZzqWnZ532  All the leaves are brown (all the leaves are b...   
4GLqrUBRMEvsNWDw3Wari1  It all started\n\nWritten on the back of a bee...   
1w3On9LuXt6VipJjV4Pqkz  These walls could use some silence\nThese eyes...   
4GdWGOxhYaI9RBKWXMFFdd  I'm sending you forget me nots\nTo help me to ...   
2u0oTsc6XcvJTh24ynQ1Ao  Hey now, you're an all star\nGet your game on,...   

                       gpt_ratings  
track_id                            
5eT5eYhcRfx9cjiflxZh8o         NaN  
2ClIt2OnPCV2gV3dZQxyBz         NaN  
6v9sCNj1KY3wblGJAohxX2         NaN  
4nYKI0JqkWfr1YbmH4ADEM         NaN  
7uJz1nHWR8TScmdnEhI8p4         NaN  
1YXq6U6yY6aQ5dkndki7KC         NaN  
1w5sLDYzYAGI0AkLc6FPlO         NaN  
6ksRossV4vKsXntCCZbhaM         NaN  
5uZlU3v9fq5ILATfqHvVwK         NaN  
3NBDgwEAGMj0aKRsU8zoO9         NaN  
1J2EmhjTmHQxLShYQK7Xti         NaN  
5WeryDMDd3BtnIIPthC7Gz         NaN  
30cW9fD87IgbYFl8o0lUze         NaN  
4zLSkwZaiMfzzapPCbdG90         NaN  
1Xq4fBayQtSJlcYZsPDY4C         NaN  
1Df5NAhInalMVZzqWnZ532         NaN  
4GLqrUBRMEvsNWDw3Wari1         NaN  
1w3On9LuXt6VipJjV4Pqkz         NaN  
4GdWGOxhYaI9RBKWXMFFdd         NaN  
2u0oTsc6XcvJTh24ynQ1Ao         NaN

In [122]:
df_half = df[10600:] # create a dataframe (to avoid printing 'not null' more than 10 thousand times when we call the API)
df_half.info() # check that there aren't many non-nulls, shows that it is 4, which is okay

<class 'pandas.core.frame.DataFrame'>
Index: 9472 entries, 5eT5eYhcRfx9cjiflxZh8o to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  9472 non-null   object
 1   gpt_ratings   4 non-null      object
dtypes: object(2)
memory usage: 222.0+ KB


In [123]:
# use the same for loop to make the API call to get the ratings 
for index, row in df_half.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_half.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null')

Getting ratings for Your love, love your love
Your love, lov
Getting ratings for Let's go
You may not see the consequence
Getting ratings for Lifetime waiting, getting busy with the 
Getting ratings for I thought I was a dreamer
But it's not a
Getting ratings for Feel the chills run down your spine
Down
Getting ratings for No, my mind ain't right
Cold, so cold la
Getting ratings for I wanna love ya
I wanna love you
And tre
Getting ratings for Heartbreaks and promises
I've had more t
Getting ratings for What would you do
To get to me
What woul
Getting ratings for We're like rivers in the night
I go lef
Getting ratings for Let's dance in style, let's dance for a 
Getting ratings for ( Mastar Vk )
Buda ju nimeomoka nikipita
Getting ratings for Always running on the move
Ain't a thing
Getting ratings for And I'm watchin' the late show
In my fla
Getting ratings for Get up on the floor
Dancing all night lo
Getting ratings for All the leaves are brown (all the leaves
Getting ratings for It al

Getting ratings for I need somethin', I know it's you, ooh-o
Getting ratings for I'm gonna love ya
Like no one could
Make
Getting ratings for Yesterday, when I was almost home
There 
Getting ratings for Infinite
W.E.G.O. (Interlude)
It's Ok
31
Getting ratings for Save me, save me, save me
Save me
You th
Getting ratings for * = letra incompleta.
 = Canción filtrad
Getting ratings for Vivo fingiendo un sueño que no se cuenta
Getting ratings for Quiero que me rompas el hocico a chupeta
Getting ratings for La vida nos cruzó
De un modo muy casual

Getting ratings for Tengo ganas de perderme entre palmeras
Q
Getting ratings for Siempre me despierto sola, pero hoy
Teng
Getting ratings for Aún recuerdo bien el sabor de tu piel
Sa
Getting ratings for Camino solo a mi destino
Pretendo no bus
Getting ratings for Esa noche pintaba aburrida
Y de pronto t
Getting ratings for Pintabas tus labios de rojo, tu pelo nar
Getting ratings for Te traigo
Un collar de besos y un trato 
Getting ratings for Me g

Getting ratings for Era un furia
Un relámpago
Un enfermedad 
Getting ratings for Te regalo mi cintura
Y mis labios para c
Getting ratings for Laura no está, Laura se fue
Laura se esc
Getting ratings for Desde que llegaste vida
Me susurran los 
Getting ratings for Rayando el sol, rayando por ti
Esta pena
Getting ratings for Cuando estabas junto a mí
Nuestra luz er
Getting ratings for Regálame tu risa
Enseñame a soñar
Con so
Getting ratings for Junte lo más hermoso
Que viví yo contigo
Getting ratings for Tú, llegaste a mi vida para enseñarme
Tú
Getting ratings for ¡Cómo quisiera poder vivir sin aire!
¡Có
Getting ratings for Quisiera darte el mundo entero
La luna, 
Getting ratings for Deja que hable
Deja que hoy te cuente
Co
Getting ratings for Un poco de ti para sobrevivir
Esta noche


KeyboardInterrupt: 

In [124]:
df_half.info() # stopped the code after some time since it was too slow, shows that it retrieved 286 ratings so far

<class 'pandas.core.frame.DataFrame'>
Index: 9472 entries, 5eT5eYhcRfx9cjiflxZh8o to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  9472 non-null   object
 1   gpt_ratings   286 non-null    object
dtypes: object(2)
memory usage: 480.0+ KB


In [127]:
# let's continue using the same for loop
for index, row in df_half.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_half.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 286 'not null's at the beginning

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

Getting ratings for Ya dime si quieres estar conmigo o si me
Getting ratings for Se me escapa el alma
Si tu no estás
Ahor
Getting ratings for Letra de "Sacúdete la arena (Remix)" ft.
Getting ratings for ¡Ay!
¡Ay, ese Carlitos!
Miren, nada más,
Getting ratings for Si río es por ti, si sueño es por ti
Si 
Getting ratings for Voy a ponerme a lavar las tazas
Pa’  ver
Getting ratings for Abriré la puerta hasta que quieras volve
Getting ratings for Cuando se apaga el amor
El corazón se qu
Getting ratings for Nacida en cuna de oro
Entre sábanas de s
Getting ratings for Llora este blues
Al anochecer
Entre past
Getting ratings for (Sonido de tacones)
Woooh!

Ábranse, per
Getting ratings for Perros callejeros, topes y baches
Tos pe
Getting ratings for * = Canciones incompletas (53)
Luis Fons
Getting ratings for Yo no entiendo de colores ni de razas
A 
Getting ratings for Habíamos acordado que no ibas a regresar
Getting ratings for Letra de "Veneno"

Lo sé, pensabas que e
Getting ratings for No t

Getting ratings for * = letra incompleta.
 = Canción filtrad
Getting ratings for Woh-oh
Baby
Ozuna
Pensándote aquí de nue
Getting ratings for Dime qué se siente ver mis ojos sin baja
Getting ratings for No he conocido a ninguno que pueda alter
Getting ratings for Nadie se imagina de lo que el silencio e
Getting ratings for Remix killer
Ñejo
Arcángel "La Maravilla
Getting ratings for Kanketbo li kan3icho, 3la moul lkoun kan
Getting ratings for Siempre el mismo ciclo
Tú en mi cama o y
Getting ratings for Oh-no, oh

Nada pasa por casualidad
Algu
Getting ratings for Siempre caigo en tu juego, no, no
Te apr
Getting ratings for Papi Déjame Ser Feliz El Es el que llena
Getting ratings for Hola (The Avengers)
Quiero saber tu nomb
Getting ratings for B. Sig in this motherfucka, holla at ya 
Getting ratings for ¡Woh!, yeah, yeah, yeah-eh, eh
Hi Music 
Getting ratings for Yo sueño que
Tú y yo estamos pasándola r
Getting ratings for No vanci no faltas (Súbelo)
El dinero no
Getting ratings for Dice

Getting ratings for No dejare de existir
Porque dentro de tu
Getting ratings for Logan Romero mami’
Jorge Milliano

Hace 
Getting ratings for Oh-nah-nah-nah (Oh-nah-nah-nah)
Oh-nah-n
Getting ratings for Let me see you work
Tráela (Woh-oh)
A to
Getting ratings for Ah-yah
(Hey, Argüello, what you do?)

Ap
Getting ratings for Kristóman dobro o decibel
Meu rap é como
Getting ratings for Yeah, yeah
Jaja, no wait
Yeah, yeah
Rare
Getting ratings for (¡The remix!)
Imagina que te quito la ro
Getting ratings for ¿En serio? (¿En serio?)
Yo sé que tus la
Getting ratings for (Nadie, eh)
Se cansó del 14 de febrero y
Getting ratings for (Ra'-Rauw)
Ojos que no ven, corazón que 
Getting ratings for Oh ! Les bras en l’air, ça peut tuer
I a
Getting ratings for Tu novio es un bobo
No se merece ninguna
Getting ratings for (Yeah; vale la pena; skrr'), yeah

Mami,
Getting ratings for Te sigo pensando (Ah-ah), no lo supero (
Getting ratings for Baby
Yeh-yeh
Este es Se'
Rudeboyz

No fu
Getting ratings for Real

Getting ratings for Cuando yo me vaya
O tu te vayas
Cuando n
Getting ratings for Por ahí dicen que tus labios (Eh, eh)
Se
Getting ratings for (Cuando te conocí; yeah; ¿dónde? ¿En qué
Getting ratings for Pasemos la trama
Saltemos directo a la c
Getting ratings for Si es que aparento es porque te miento
J
Getting ratings for No sé qué paso ahora
Dime, me tienes aqu
Getting ratings for Yeah yeah, ay
Soon as you come over, It'
Getting ratings for D-Note Is On The Beat
Tú sabes lo que yo
Getting ratings for Llevo tiempo dando vueltas
Pensando en l
Getting ratings for Estar contigo por siempre; eso yo quisie
Getting ratings for (Ah, ah-ah)
It's the game changer
(Ah, a
Getting ratings for Hoy a la disco llegó sola
Porque su amig
Getting ratings for Selena Gomez - Lose You To Love Me
Selen
Getting ratings for Lo' verdadero'

Me llama privado, pero y
Getting ratings for I miei miti sono morti nella guerra musi
Getting ratings for Em nome do pai, do filho, do Espírito Sa
Getting ratings for Mmmm

Getting ratings for (Los Extraterrestres)
Ajá, otra dimensió
Getting ratings for Bailando asi
Tu no sabes como me provoca
Getting ratings for Y niki-guay-guay-guay
Nanarana-nana, nan
Getting ratings for Boom! You ready?

(¡Oh-oh!) Me quiere be
Getting ratings for Yankee, métele con candela, Yankee, méte
Getting ratings for Siento que (Siento que)
Algo cambió (Cam
Getting ratings for La Mente Maestra

Le pido consejo' pa' s
Getting ratings for Oh-ah
Ey, singing your song
Nota Loca (E
Getting ratings for Eli re eli, kya hai yeh paheli
Aisa vais
Getting ratings for Tú piensas en mí
(Luney Tunes! Siggy-Da,
Getting ratings for Yo'
Estos son Los Pitbulls
¡Nesty!
Aauf!
Getting ratings for Ey, ey, mami, no dejes para mañana lo qu
Getting ratings for Ey
Uh, yeah, yeah
¡Los Extraterrestres!

Getting ratings for La Mente Maestra
Hace rato que tu mirada
Getting ratings for Si esa almohada hablara
Si las paredes h
Getting ratings for * = letra incompleta.01/05Mozart La Para
Getting ratings for Si t

KeyboardInterrupt: 

In [126]:
df_half.info()  # I stopped the loop above to check the progress and re-ran it twice

<class 'pandas.core.frame.DataFrame'>
Index: 9472 entries, 5eT5eYhcRfx9cjiflxZh8o to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  9472 non-null   object
 1   gpt_ratings   934 non-null    object
dtypes: object(2)
memory usage: 480.0+ KB


In [128]:
df_half.info() # it retrieved 1499 ratings so far

<class 'pandas.core.frame.DataFrame'>
Index: 9472 entries, 5eT5eYhcRfx9cjiflxZh8o to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  9472 non-null   object
 1   gpt_ratings   1499 non-null   object
dtypes: object(2)
memory usage: 480.0+ KB


In [129]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_half['gpt_ratings']) # fill the nulls in the larger dataframe
df.info() # check that there are around 12 thousand ratings

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   12099 non-null  object
dtypes: object(2)
memory usage: 986.5+ KB


In [130]:
df.to_csv('first_twelve_thousand_ratings.csv') # save the dataframe to a csv for backup

In [140]:
df[12095:].head(20) # find the index where null values for ratings start

track_lyrics  \
track_id                                                                    
5fwFQ9hooBZoxdboAHo99Y  Ya no sonríe más\nSe arregla toda\nSi va a la ...   
5Ji2qD1v0TGC5dlKIYA6Oo  Cuando hay sol en la mañana, ahí es que detona...   
0aCjE4cpIQxLQcaNAj1xgW  Ronca\nProbando\n¿Eliel, tú me escucha'? (¡Arr...   
5c84PdxrNFJnJXXb7JiaoZ  Letra de "Slow Motion (ft. Syko)"\n\nMujeres s...   
12ajClWUHnrqZOeefJxVsU  Sé que me miras así\nYo como que te conozco\nY...   
42QpgFFhu8SIKFK2dp0kUj  Letra de "Vacaciones (Remix)" ft. Tito 'El Bam...   
7AObnx2EzL6FeYjmdjPCoA  Linkon\nRobin\nEl Orfanato\n\nLa conocí una ta...   
7uIRZRw4xM2IcfCP1sSwnD  El mundo va a matarse pa' lo oscuro\nOh-oh\nCa...   
3K0jtXM4i435C6dFQWvgWr  Multimillo Records\nRa-pam-pam-pam\n\nElla es ...   
15a5yBoHJhHHWjKbyLO10s  Le dio calor, se está quitando la camisa\nPoqu...   
38yQMFhgXnTFYOnxrbOv9v  Ayer te vi\nY senti que en tu vida ya no exist...   
4joRJ9BbN4S3PxvCehX73Y  Se cansó de llorar\nY condenó su corazón a una...   
7qvWz9AsvPmXlIWZ94VFpj  Knignt Rydaz\nRobin, Lex\n¡Robin! (¡Yeah!), ¡L...   
5xPgLR8hKsPWlOBnurBi20  Yo nací en la isla del encanto, Puerto Rico\n1...   
199yJpWCdPhon2nlmLslJI  Letra de "Dure Dure" ft. Don Omar\nQue dure\n\...   
03wOwEbTS3JR2Y2U0TxkFx  Desde que te hablé sabía que eras especial, ex...   
7yxWmnTrXBxevDiMf2qrqI  Otra luna llena\nY tú no me llamas\nDe ti no s...   
4ETrFf4SEWUyvQRtnB2ibm  Don\nMike Stanley\n"El Rey"\nD-D-D\nD-D-D\nD-O...   
18Phat5S6ck3pIJItSA9GS  Yo tengo celos de ti, woh oh\nTengo envidia de...   
3spqYs23KuMYNRDv0ReTEK  Eliel\nDon! Don!\n\nQuisiera pasar la noche ba...   

                                    gpt_ratings  
track_id                                         
5fwFQ9hooBZoxdboAHo99Y  7 6 7 7 5 7 6 5 5 4 5 6  
5Ji2qD1v0TGC5dlKIYA6Oo                      NaN  
0aCjE4cpIQxLQcaNAj1xgW                      NaN  
5c84PdxrNFJnJXXb7JiaoZ                      NaN  
12ajClWUHnrqZOeefJxVsU                      NaN  
42QpgFFhu8SIKFK2dp0kUj                      NaN  
7AObnx2EzL6FeYjmdjPCoA                      NaN  
7uIRZRw4xM2IcfCP1sSwnD                      NaN  
3K0jtXM4i435C6dFQWvgWr                      NaN  
15a5yBoHJhHHWjKbyLO10s                      NaN  
38yQMFhgXnTFYOnxrbOv9v                      NaN  
4joRJ9BbN4S3PxvCehX73Y                      NaN  
7qvWz9AsvPmXlIWZ94VFpj                      NaN  
5xPgLR8hKsPWlOBnurBi20                      NaN  
199yJpWCdPhon2nlmLslJI                      NaN  
03wOwEbTS3JR2Y2U0TxkFx                      NaN  
7yxWmnTrXBxevDiMf2qrqI                      NaN  
4ETrFf4SEWUyvQRtnB2ibm                      NaN  
18Phat5S6ck3pIJItSA9GS                      NaN  
3spqYs23KuMYNRDv0ReTEK                      NaN

In [141]:
df_second_half = df[12095:] # create another dataframe from this index on
df_second_half.head() # double check by showing the first 5 rows

track_lyrics  \
track_id                                                                    
5fwFQ9hooBZoxdboAHo99Y  Ya no sonríe más\nSe arregla toda\nSi va a la ...   
5Ji2qD1v0TGC5dlKIYA6Oo  Cuando hay sol en la mañana, ahí es que detona...   
0aCjE4cpIQxLQcaNAj1xgW  Ronca\nProbando\n¿Eliel, tú me escucha'? (¡Arr...   
5c84PdxrNFJnJXXb7JiaoZ  Letra de "Slow Motion (ft. Syko)"\n\nMujeres s...   
12ajClWUHnrqZOeefJxVsU  Sé que me miras así\nYo como que te conozco\nY...   

                                    gpt_ratings  
track_id                                         
5fwFQ9hooBZoxdboAHo99Y  7 6 7 7 5 7 6 5 5 4 5 6  
5Ji2qD1v0TGC5dlKIYA6Oo                      NaN  
0aCjE4cpIQxLQcaNAj1xgW                      NaN  
5c84PdxrNFJnJXXb7JiaoZ                      NaN  
12ajClWUHnrqZOeefJxVsU                      NaN

In [142]:
# retrieve ratings using the dataframe with roughly the second half of the data to avoid printing a lot of 'not null's
for index, row in df_second_half.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_second_half.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 'not null' only once

not null
Getting ratings for Cuando hay sol en la mañana, ahí es que 
Getting ratings for Ronca
Probando
¿Eliel, tú me escucha'? (
Getting ratings for Letra de "Slow Motion (ft. Syko)"

Mujer
Getting ratings for Sé que me miras así
Yo como que te conoz
Getting ratings for Letra de "Vacaciones (Remix)" ft. Tito '
Getting ratings for Linkon
Robin
El Orfanato

La conocí una 
Getting ratings for El mundo va a matarse pa' lo oscuro
Oh-o
Getting ratings for Multimillo Records
Ra-pam-pam-pam

Ella 
Getting ratings for Le dio calor, se está quitando la camisa
Getting ratings for Ayer te vi
Y senti que en tu vida ya no 
Getting ratings for Se cansó de llorar
Y condenó su corazón 
Getting ratings for Knignt Rydaz
Robin, Lex
¡Robin! (¡Yeah!)
Getting ratings for Yo nací en la isla del encanto, Puerto R
Getting ratings for Letra de "Dure Dure" ft. Don Omar
Que du
Getting ratings for Desde que te hablé sabía que eras especi
Getting ratings for Otra luna llena
Y tú no me llamas
De ti 
Getting ratings

Getting ratings for Rolling in my motherfucking rag-top Chev
Getting ratings for Drop one for the treble, two for the bas
Getting ratings for An eye for an eye's how the fuck we feel
Getting ratings for : Ese Daz
Come fly with me (Let's get hi
Getting ratings for I hope you don't mind
But I'd like to st
Getting ratings for CoRo
Ella se fue...
Aún me acuerdo cuand
Getting ratings for Que bonita es la vida, y que bonito es e
Getting ratings for Sabes que Conejo
You gotta put it down
F
Getting ratings for Triple C clique droppin' somethin' to bu
Getting ratings for Aquí estoy thinking about you carnalito

Getting ratings for Let me tell you about my hood, let me te
Getting ratings for Intro:
You Know Baby
When I Didn't Have 
Getting ratings for I'm here for you girl for whatever you n
Getting ratings for I got this mother fucker staring at me
S
Getting ratings for Check It Out Lil Homies
This Is What I W
Getting ratings for Yo what's up? C.L.S is in the house, you
Getting ratings for Get 

Getting ratings for The universe is inside your eyes
Bright 
Getting ratings for Es que con tu piel me envuelves (Prr, pr
Getting ratings for (Yo soy Reykon "El Líder")
(E-E-E-Evos J
Getting ratings for La Rosalía, uh

Que jo sé que he nascut 
Getting ratings for Yo me la paso trabajando y joseando
Y cu
Getting ratings for Si tuviera que definir
Todo esto que sie
Getting ratings for (Hey) (Jaja)
Iah-iah-yeh-yeh
Piri-piri-p
Getting ratings for (Vamo' a afincar la cosa)
Ey, bienvenido
Getting ratings for No puedo confiar (No, no), en nadie conf
Getting ratings for Eh, eh
Uoh, uh-yeh
Myke Towers
Ra-Rauw
(
Getting ratings for Me voy a olvidar, me voy a olvidar, me v
Getting ratings for This is the remix
Son las doce, tú me di
Getting ratings for Eh, yao
Cuando quieras llamarme
Arcángel
Getting ratings for Just gonna stand there and watch me burn
Getting ratings for Went from Mr. 305 (Dade County)
To Mr. W
Getting ratings for Girl, my body don't lie (RedOne)
I'm out
Getting ratings for For 

Getting ratings for I want you
I want you so bad
I need you

Getting ratings for Shawty say she love me now
I don't think
Getting ratings for Een rij met mensen en ze kijken allemaal
Getting ratings for Loving you is like playing with dynamite
Getting ratings for Cool Johnski from the Freeze Force Crew

Getting ratings for All I want's a friend and you want mine

Getting ratings for I got that this feeling that
My dreams'l
Getting ratings for Cuando te conocí tu fuiste para mí
Un su
Getting ratings for Every morning I'm feeling
Afternoon it's
Getting ratings for Cold enough to chill my bones
It feels 
Getting ratings for Once, I was seven years old, my mama tol
Getting ratings for Well, you only need the light when it's 
Getting ratings for I'm only one call away
I'll be there to 
Getting ratings for Hmm-mmm-mmm
Woah-oh-oh-oh
It's always a 
Getting ratings for Same bed, but it feels just a little bit
Getting ratings for Here I am waiting, I'll have to leave so
Getting ratings for Ho! H

Getting ratings for Hmm, uh
Na-na-na-na
D-Denta on the, yeah
Getting ratings for Ik was in de field met je
4 handen, 1 bu
Getting ratings for Aye, 1,2,3, myew myew myew, myew myew my
Getting ratings for Songtekst van Broederliefde – "Hoe Je Be
Getting ratings for Ik zei d’r: ”Kom weg, doe je jas aan”
Ik
Getting ratings for Songtekst van Broederliefde – "Officieel
Getting ratings for Yu-yu-yu-yung Felix
Bizzey

Oh na
Shaka,
Getting ratings for Hoy esperé tu llamada como antes
Planee 
Getting ratings for Como la lluvia que te moja en las mañana
Getting ratings for Ando armado y peligroso
Coronando victor
Getting ratings for Hey
Oh no
Madiel Lara on the beat bro
Fr
Getting ratings for Mi pasado no existe más
Ya dejé todo atr
Getting ratings for Mente piensa en gloria
Cuerpo asciende g
Getting ratings for No tengo tiempo, para esperar
Sigo adela
Getting ratings for The name is E.D
Ed
I got some rust to sh
Getting ratings for Yo contigo siento que vuelo
Y lo que tu 
Getting ratings for One,

Getting ratings for Ain't got nobody, baby...baby

Check thi
Getting ratings for Como cada viernes la raza está presente

Getting ratings for Ya estuvo? You're stupid!
Ya estuvo, hol
Getting ratings for Lo mío es más Chomsky lo tuyo es más Fon
Getting ratings for (Live and direct)
(Live and direct)
(Liv
Getting ratings for Looks complicated, huh, but when the sou
Getting ratings for A veces quisiera desaparecer del mapa
Vo
Getting ratings for I'm predisposed for abuse I can take it 
Getting ratings for Cuando el juego se hace verdadero
Cuando
Getting ratings for Somos humanos animales trabajando en lo 
Getting ratings for And I looked and behold a pale horse
And
Getting ratings for Papi ¿donde esta el funk?
Quiero saber d
Getting ratings for He estado prendiendo inciensos, dejé de 
Getting ratings for Yeah, ja
Y qué ¿más chimba allá o mas ch
Getting ratings for SUAVE Y SUDA
BAILA CON FRESCURA
ERES ESC
Getting ratings for "Ojos de diablo" dice la doña, por ahí f
Getting ratings for Llav

KeyboardInterrupt: 

In [143]:
df_second_half.info() # stop the code and check the progress, 795 ratings so far

<class 'pandas.core.frame.DataFrame'>
Index: 7977 entries, 5fwFQ9hooBZoxdboAHo99Y to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  7977 non-null   object
 1   gpt_ratings   795 non-null    object
dtypes: object(2)
memory usage: 445.0+ KB


In [144]:
# continue with the same code
for index, row in df_second_half.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_second_half.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 795 'not null's at the beginning

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

Getting ratings for Ey

E-E-E-E, En la calle se comenta que 
Getting ratings for Hace tiempo que nuestra comunicación
Es 
Getting ratings for Oh oh oh oh oh oh
Tu dime quien mas
Eh e
Getting ratings for Dime cuanto quieres esperar
Para nuestra
Getting ratings for Si yo lo que quiero es compartir contigo
Getting ratings for A ella no le importa lo que diga la gent
Getting ratings for La noche está buena pa que te tires
(est
Getting ratings for Letra de "Se Acabó El Amor"
Bringing the
Getting ratings for * = letra incompleta.01/10Kevin Roldan -
Getting ratings for Esto e' una melodía maravillosa

Ella as
Getting ratings for Mírala, donde va por ahí (Donde va por a
Getting ratings for Y pa que te..
Yaauu (yauu)
Remix
Gotay
E
Getting ratings for Súbelo, que Farru llego (Mmm)
Ando por a
Getting ratings for Y esta noche vine
Pa toa, p atoa, p atoa
Getting ratings for She asked me as if she knew nothing (Oh,
Getting ratings for Tú la ve', tú la ve', tú la ve'
Tú la ve
Getting ratings for AXL


Getting ratings for You've got me all in my feelings
Girl, I
Getting ratings for Harry Styles - Lights Up
Camila Cabello 
Getting ratings for You might say that I am crazy
But tell m
Getting ratings for Over and over again
How many times you g
Getting ratings for Pocket with the Fendi, too filled up
Sho
Getting ratings for Everybody knows you don't (Everybody kno
Getting ratings for Joro, joro, joro, joro, joro, joro, joro
Getting ratings for CashMoneyAP
Oh-oh, oh-oh
Yeah

I knew on
Getting ratings for $k on it

I can see that ass from the fr
Getting ratings for One, two, three, four

Never sleep 'caus
Getting ratings for Yeah, pull up
Let me do my dance
Send th
Getting ratings for You ain't never too much
I ain't in no r
Getting ratings for Don't keep leading me on
I know just wha
Getting ratings for Miiri man ɲi!
Aa! dennin! k'an bɛn sɔgɔm
Getting ratings for Camila Cabello - Liar
Post Malone - Sain
Getting ratings for Yeah, inside di ting dem call sweet melo
Getting ratings for I do

Getting ratings for Baby baby, baby baby
Baby baby, baby bab
Getting ratings for So sad to see you go so soon (So soon)
I
Getting ratings for For you I give a lifetime of stablility

Getting ratings for With all my heart, I love you, baby
Stay
Getting ratings for I knew God was, was with me
I always use
Getting ratings for Sat up in the dark for so long
Just livi
Getting ratings for Hee...
Shoop-de-bop
Funky pops

Coffee, 
Getting ratings for Oh yeah baby
You got to make your mind u
Getting ratings for J. Holiday
Oo-oh, oo-oh
(Ay-ay-ay, Ay, A
Getting ratings for Let me lay it on the line
I got a little
Getting ratings for I never knew such a day could come
And I
Getting ratings for There are times when I look above and be
Getting ratings for Easy way to leave easy way to go
Easy wa
Getting ratings for It's undeniable
That we should be toget
Getting ratings for Your love's so good (Oh)
I got to testif
Getting ratings for I know this might sound crazy
But I don'
Getting ratings for Ladie

Getting ratings for Some people live for the fortune
Some p
Getting ratings for I miei fra contrabbandano animali
Fanno 
Getting ratings for You've got the words to change a nation 
Getting ratings for I'm jealous of the rain
That falls upon 
Getting ratings for You and me we made a vow
For better or 
Getting ratings for Help, I have done it again
I have been h
Getting ratings for Oh, misty eye of the mountain below
Keep
Getting ratings for Somebody said you got a new friend
But d
Getting ratings for You tell all the boys "No"
Makes you fee
Getting ratings for I spent my time watchin'
The spaces that
Getting ratings for Now that I am sober
I take back what I s
Getting ratings for Dime porque hasta aquí me trajo el tiemp
Getting ratings for It's been 5 years I still love everythin
Getting ratings for He gives another smile, tries to underst
Getting ratings for I do love you but it's
I do love you but
Getting ratings for And oh, you're gonna love me
You're gonn
Getting ratings for I've l

...

Getting ratings for Avremo segni sulle mani
E le occhiaie de
Getting ratings for Não, acho que eu entrei num grupo bom
Es
Getting ratings for Kickoff got the sauce

Wanneer je denkt 
Getting ratings for Procuro a paz, procuro a paz

Procuro a 
Getting ratings for Fases ruins renderam mil frases boas
Jun
Getting ratings for Sabe que eu tô doido pra te ver de novo

Getting ratings for {Verse 1}
Eu não posso esperar
Linda pre
Getting ratings for Acertei mais um
No tambor ainda tem cinc
Getting ratings for Hoje eu vou te contar
Faz tempo que as c
Getting ratings for Louca
Você me chama de louca
Mas logo lo
Getting ratings for Eu quero você e mais ninguém
Não quero m
Getting ratings for I'm going to die
So are you. Your spouse
Getting ratings for Viajo e sempre paro em você aqui
Guardo 
Getting ratings for Kamika-z

E o nosso plano
Que ontem à no
Getting ratings for MilFlows, aham
Como que tu chega sem avi
Getting ratings for Mulher, 'cê gosta quando o corpo fica em
Getting ratings for "No 

Getting ratings for I can explain and justify
And make excus
Getting ratings for Ah yeah, yeah, yeah, yeah, yeah
Yeah, ye
Getting ratings for Baby, baby, baby

If you found somebody 
Getting ratings for Woah-oh-oh, yeah
Woah-oh-oh, yeah
I don'
Getting ratings for Tú sabes que mi cama es bien buena
Y ya 
Getting ratings for You got the black belt, I got the gun
Le
Getting ratings for total: 113🌱 - my favorite listens
👹 - my
Getting ratings for Said I'd never fall, I'd never fall, I'd
Getting ratings for Only think about him on the weekdays and
Getting ratings for Crowded bar, corner booth
It's getting h
Getting ratings for Translations Español Türkçe Français Dan
Getting ratings for Coat, laying on the floor
Long December 
Getting ratings for FKA twigs - sad day
MC Kevin o Chris - E
Getting ratings for Happiness
Ain't something you sit back a
Getting ratings for Can I just record you doing that?
Is it 
Getting ratings for Don't think that I didn't notice this co
Getting ratings for (Hus

Getting ratings for Old man, look at my life, I'm a lot like
Getting ratings for There's a lady who's sure 
All that gli
Getting ratings for It's knowing that your door is always op
Getting ratings for Backstroke lover
Always hidin' 'neath th
Getting ratings for Karma police
Arrest this man, he talks i
Getting ratings for Face down in the river, my love
Face dow
Getting ratings for Very superstitious, writing on the wall
Getting ratings for Hey little girl is your daddy home?
Did 
Getting ratings for :
You are listening to (scallops hotel, 
Getting ratings for Heah hah hah!  
I'm serious nigga one o
Getting ratings for Like the legend of the phoenix
All ends 
Getting ratings for She was more like a beauty queen from a 
Getting ratings for I'm gonna fight 'em off
A seven nation a
Getting ratings for When the truth is found
To be lies
And a
Getting ratings for Say your prayers little one
Don't forget
Getting ratings for Just one look and I fell so hard
In love
Getting ratings for My baby

Getting ratings for Ci siamo capiti male
Ma siamo capitati b
Getting ratings for Il mio primo bacio è nel 2006
Le ho dett
Getting ratings for Io che nemmeno ti piacevo
Io che nemmeno
Getting ratings for Milano Dateo sulla mappa è un neo
Ma ci 
Getting ratings for Strofino via i sogni dagli occhi
I miei 
Getting ratings for Che ti ricordi di me lo so
Ma solo quand
Getting ratings for Ah, ah

I sob in pain, I call your name

Getting ratings for Mi svegliai
Tentennai, me ne andai, yeah
Getting ratings for Lo so che eri abituata a fidarti solo di
Getting ratings for Quand'è che spento il cuore?
Che ho smes
Getting ratings for Sorriderai
E ti rivedo come sei
Incrocer
Getting ratings for Bevevamo controvoglia liquore al sambuco
Getting ratings for Portami via da qua con te, potrà sembrar


KeyboardInterrupt: 

In [145]:
df_second_half.info() # stopped the code above check the status here, 2175 ratings so far

<class 'pandas.core.frame.DataFrame'>
Index: 7977 entries, 5fwFQ9hooBZoxdboAHo99Y to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  7977 non-null   object
 1   gpt_ratings   2175 non-null   object
dtypes: object(2)
memory usage: 445.0+ KB


In [146]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_second_half['gpt_ratings']) # fill the nulls in the larger dataframe
df.info() # check the number of non-nulls in the larger dataframe, around 14k as expected

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   14270 non-null  object
dtypes: object(2)
memory usage: 986.5+ KB


In [147]:
df.to_csv('first_fourteen_thousand_ratings.csv') # let's save these to a csv as well

In [150]:
df[14265:].head(10) # find the index where nulls start in the gpt_ratings

track_lyrics  \
track_id                                                                    
09YXhYMYIHZBHVKGEQrSQF  Quand'è che spento il cuore?\nChe ho smesso di...   
3zX26vtXy3tRbbKPEQTaTD  Sorriderai\nE ti rivedo come sei\nIncrocerai\n...   
23hpOtox5sIuRqVBVVJxsO  Bevevamo controvoglia liquore al sambuco\nE io...   
2qS8NRov7B0s5zhF7wzy46  Portami via da qua con te, potrà sembrarti pre...   
2QeCyjLDJ6qDJsCyofrEW9  Delle cose che dici ne conosco la metà\nE di t...   
1HOjSh3MEhxd3xJAgcmyLC  Oh-oh-oh\nOh-oh-oh\n\nNon ne posso più di ques...   
1ABG6ke9SdUK9YayVafbcX  Come l'aria mi respirerai\nIl giorno che\nTi n...   
2eXLx58ykMF6jayu2WZpPt  Il tramonto nei tuoi occhi, e nel mare blu\nC'...   
2ReQoOCGRsychjlu0bQH1U  Dolceamaro\nDolceamaro\n(Dolceamaro)\n\nDolcea...   
77Gcau9O0kh48tlerpi6rX  Mi sono ritrovato qui, quanto tempo che è pass...   

                                    gpt_ratings  
track_id                                         
09YXhYMYIHZBHVKGEQrSQF  8 7 8 8 7 8 6 5 3 3 4 6  
3zX26vtXy3tRbbKPEQTaTD  8 6 8 7 6 8 3 4 3 4 3 5  
23hpOtox5sIuRqVBVVJxsO  7 8 8 8 7 8 6 6 5 4 6 7  
2qS8NRov7B0s5zhF7wzy46                      NaN  
2QeCyjLDJ6qDJsCyofrEW9                      NaN  
1HOjSh3MEhxd3xJAgcmyLC                      NaN  
1ABG6ke9SdUK9YayVafbcX                      NaN  
2eXLx58ykMF6jayu2WZpPt                      NaN  
2ReQoOCGRsychjlu0bQH1U                      NaN  
77Gcau9O0kh48tlerpi6rX                      NaN

In [151]:
df_last_quarter = df[14265:] # create a subset starting on this index
df_last_quarter.head() # double check by printing the first 5 rows

track_lyrics  \
track_id                                                                    
09YXhYMYIHZBHVKGEQrSQF  Quand'è che spento il cuore?\nChe ho smesso di...   
3zX26vtXy3tRbbKPEQTaTD  Sorriderai\nE ti rivedo come sei\nIncrocerai\n...   
23hpOtox5sIuRqVBVVJxsO  Bevevamo controvoglia liquore al sambuco\nE io...   
2qS8NRov7B0s5zhF7wzy46  Portami via da qua con te, potrà sembrarti pre...   
2QeCyjLDJ6qDJsCyofrEW9  Delle cose che dici ne conosco la metà\nE di t...   

                                    gpt_ratings  
track_id                                         
09YXhYMYIHZBHVKGEQrSQF  8 7 8 8 7 8 6 5 3 3 4 6  
3zX26vtXy3tRbbKPEQTaTD  8 6 8 7 6 8 3 4 3 4 3 5  
23hpOtox5sIuRqVBVVJxsO  7 8 8 8 7 8 6 6 5 4 6 7  
2qS8NRov7B0s5zhF7wzy46                      NaN  
2QeCyjLDJ6qDJsCyofrEW9                      NaN

In [152]:
# use the same for loop on the new subset dataframe with roughly the last 5k lyrics
for index, row in df_last_quarter.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_last_quarter.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 'not null' only a few times

not null
not null
not null
Getting ratings for Portami via da qua con te, potrà sembrar
Getting ratings for Delle cose che dici ne conosco la metà
E
Getting ratings for Oh-oh-oh
Oh-oh-oh

Non ne posso più di q
Getting ratings for Come l'aria mi respirerai
Il giorno che

Getting ratings for Il tramonto nei tuoi occhi, e nel mare b
Getting ratings for Dolceamaro
Dolceamaro
(Dolceamaro)

Dolc
Getting ratings for Mi sono ritrovato qui, quanto tempo che 
Getting ratings for Questa notte senza luna è luna nera
Sta 
Getting ratings for Prima che diventi giorno
Voglio stare an
Getting ratings for E vote me domande si l'ammore è sul 'na 
Getting ratings for Non so nemmeno più da quanto non ti sent
Getting ratings for Io sono cresciuto in strada
Uebe, propri
Getting ratings for Che giornata, che giornata
So' distrutto
Getting ratings for Da sottoterra al cielo sono trenta piani
Getting ratings for Penso a te quando mi perdo
Dentro il vuo
Getting ratings for Hai gli occhi di tuo padre
La bocca di

Getting ratings for "Hi! We're not in right now
But if you l
Getting ratings for We don't even have to talk about it
Just
Getting ratings for "Stay"
Stay (x3)
Stay baby
Stay, come on
Getting ratings for Calling all cars

I never thought that
I
Getting ratings for I was like peace in a groove
On a Sunday
Getting ratings for My girls like candy, a candy treat
She 
Getting ratings for I saw you (And him, and him) walking in 
Getting ratings for Don't wake me, I'm dreaming (doooooo)
Do
Getting ratings for Oh, uh
Feels good
Everybody
(Oh, oh, oh;
Getting ratings for Last night, I had the time of my life
It
Getting ratings for I am the Lyte as— as a rock L-Y— L— L-Y-
Getting ratings for You know it's about three o'clock when I
Getting ratings for Ooh baby, give it to me now, girl, yeah

Getting ratings for When I'm alone in my room sometimes I st
Getting ratings for (Merry go round and round)
Ho, ho, no
I'
Getting ratings for Aouw! (Ooh)
Aouw!

I took my baby on a S
Getting ratings for But t

Getting ratings for You never try me
Always stood right by m
Getting ratings for Don't wanna be a player
Don't wanna be a
Getting ratings for My dear-my dear-my dear you do not know 
Getting ratings for (Cryin', cryin', cryin')
Yeah, what’s up
Getting ratings for Back to the B-B-Brown
Back to the B-B-Br
Getting ratings for Rock on
Acknowledge my song
Bring my pos
Getting ratings for Gimme the track
Stop
Everybody on the fl
Getting ratings for Let me see you pop that thang
Shake that
Getting ratings for Da-ding-de-ding-de ding-de-de-de-ding-di
Getting ratings for *Guy Talking*
Get on, get on nigga thoug
Getting ratings for “Girl, he had nerve to have an attitude 
Getting ratings for Mama was a fallen angel
Papa was a rolli
Getting ratings for Drums Please!

Summer, summer, summertim
Getting ratings for Mm, yeah
Check it out, baby
Make it hot,
Getting ratings for Yeah, Mýa
RedZone, what, what?
Uh

It's 
Getting ratings for All I want is somebody who's gonna love 
Getting ratings for (Sis

Getting ratings for Uhhhh, uhhhh
Haah, haah, haah, haah
This
Getting ratings for Word to mother, got my nigga Buck 3000 o
Getting ratings for Yeah, this how it's goin' down, nigga, R
Getting ratings for Yeah...
I feel the rain comin' down on m
Getting ratings for Yeah, yeah, yeah
Where all my
Uhh, yeah

Getting ratings for Hussein Fatal:
Yeah My Nigga Rule, Husse
Getting ratings for (Murder Inc.)
What's my motherfuckin' na
Getting ratings for Murder Inc. shit
Uh... uh, uh, uh

Now e
Getting ratings for (Yeah)
Right off the back, ma, the boy g
Getting ratings for Here's the old school with the new schoo
Getting ratings for Love it, baby (Love it, baby, love it, b
Getting ratings for Dirty South, can y'all really feel me?
E
Getting ratings for Passion, instant
Sweat beads, feel me
Cu
Getting ratings for Yeah this is for my brothers in the hood
Getting ratings for Girl...
Yo, why you wanna play me like t
Getting ratings for Girl it seems like only yesterday
That I
Getting ratings for Oooo

Getting ratings for Yo, get, get up on the TLC tip
Yo, get, 
Getting ratings for All the lonely nights, I spend alone
Nev
Getting ratings for Boy, be quiet, follow me and tip toe
Don
Getting ratings for You got me singin'
Because of love (Very
Getting ratings for I never knew what I was missing
Love wit
Getting ratings for Like a star in the sky
That shines so br
Getting ratings for In the thundering rain
You stare into my
Getting ratings for We'd like to introduce us
We're Color Me
Getting ratings for Jezebel, wasn't born
With a silver spoon
Getting ratings for Look at the bargains over here, ladies

Getting ratings for I won't pretend that I intend to stop li
Getting ratings for Give it to me, baby
Give it to me

I'm t
Getting ratings for I gave you love
You did me wrong
I didn'
Getting ratings for I can't disguise the pounding of my hear
Getting ratings for I'm not a woman
I'm not a man
I am som
Getting ratings for Ayo, T-Roni,  I really like this guy
But
Getting ratings for As I wa

...

Getting ratings for To read the lyrics, click on the song yo
Getting ratings for 部屋の窓辺で
夜をほどいた
君の瞳は
まだ夕暮れの波
肌に染まった
香りあやして
Getting ratings for 上を向いて歩こう
涙がこぼれないように
思い出す春の日
一人ぼっちの夜

上を向
Getting ratings for シンプル・ラブ
考えすぎねあなた
シンプル・ラブ
心の向くまま
私の腕が
居心地
Getting ratings for 熱い砂けむり上げて　走るジープを見たよ
それは恋に憑かれた　悲しいハンター
渇い
Getting ratings for 今は夏　そばにあなたの匂い
しあわせな夢におぼれていたけれど
夕立ちが白い稲妻つ
Getting ratings for Through the window
影のように
街並みを染めあげる
暗いtwi
Getting ratings for Midnight pretenders
背中のホクロを なぞれば
にじむ 涙 U
Getting ratings for グラス空ける度に　ワインを注ぐだけじゃ
からっぽのハートは　とても満たせやしない
Getting ratings for Hotelのバーラウンジ
誰もが共犯者めいて
モナリザの微笑み
視線で合図する

Getting ratings for Um, dois
Um, dois, três, quatro

あなたにとって
Getting ratings for 冬空に架る　Rainbow
風は運んでくる
あなたとつないだ手の　甘いぬくもり

Getting ratings for 激しさと、この胸の中で絡み付いた灼熱の闇
Expose yourself
朦朧の
Getting ratings for 冬の波荒れてた
夕暮れ 見送る
海のテラス
電話して来たわと
そっと君は
まつ毛
Getting ratings for Car radio 流れる せつなすぎるバラードが
友達のライン こわしたの
き
Getting ratings for (Intro)
The parody has begun
Ladies and 
Getting ratings for 5/2


Getting ratings for RIOWONDERFULLIGHT RIVER CITY SOUL = RIOL
Getting ratings for I've been wearing faces in the strangest
Getting ratings for Hey now
Feel real good today this is the
Getting ratings for This road is gon’ take us back now
You l
Getting ratings for I don't wanna write this down
I wanna te
Getting ratings for You know, baby
I know you think we can m
Getting ratings for Tell me how, baby
Could it open my eyes

Getting ratings for I would be you, you would be me, we woul
Getting ratings for Enjoy ya Self, Enjoy ya Self, Enjoy ya S
Getting ratings for Shout it like a stereo, I'm not your ste
Getting ratings for So long, you did me wrong
So long, you d
Getting ratings for Now I don't
I used to love him but now I
Getting ratings for Broken hearts everywhere
From stepping o
Getting ratings for "Now keep in mind that I'm an artist
And
Getting ratings for Ooh, I promise not to do it again
I prom
Getting ratings for The Sun, the sun don't wait for nothing,
Getting ratings for Alri

Getting ratings for Honey, load up your questions
And pick u
Getting ratings for Darling, please, we were too gone to sta
Getting ratings for Babe
There's something tragic about you

Getting ratings for Oh we've waded out
'Cross the boiling oc
Getting ratings for We're bound to wait all night
She's bou
Getting ratings for : Baby Bash
Step in the club like it ain
Getting ratings for If you keep leaving me
I'll keep loving 
Getting ratings for When I'm feelin' blue
And no light is sh
Getting ratings for Well I walked over the bridge
Into the c
Getting ratings for I want love, but it's impossible
A man l
Getting ratings for Love has a way
(Of blaming the darkness)
Getting ratings for Tonight you're mine completely
You give 
Getting ratings for Bound, bound
Bound, bound
Bound to fall 
Getting ratings for It's summertime and the living is easy
F
Getting ratings for Won't you tell me to my face
If I'm boun
Getting ratings for Lay my heart down, laid it down for you

Getting ratings for I've 

Getting ratings for (Exterminator)
(Exterminator)

(Extermin
Getting ratings for You can take my-
You can take my bass do
Getting ratings for And if he's gonna follow me, he better h
Getting ratings for Don't pause, press play
Don't pause, pre
Getting ratings for Now everyday we look up at the ceiling
W
Getting ratings for These fly rhymes and high times are brou
Getting ratings for My love, my love
Don't go, don't go
Don'
Getting ratings for Chef Nay making fire

I am spitting all 
Getting ratings for Four dark riders, the black demons of Re
Getting ratings for Hi, my name is Siri
I'm a humanized arti
Getting ratings for Bring the house down
Bring the

It is ou
Getting ratings for I knew that it could be a sound of the f


KeyboardInterrupt: 

In [153]:
df_last_quarter.info() # shows that 1905 ratings are retrieved so far

<class 'pandas.core.frame.DataFrame'>
Index: 5807 entries, 09YXhYMYIHZBHVKGEQrSQF to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  5807 non-null   object
 1   gpt_ratings   1905 non-null   object
dtypes: object(2)
memory usage: 265.1+ KB


In [154]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_last_quarter['gpt_ratings']) # fill the nulls in the larger dataframe
df.info() # check the number of non-nulls in the larger dataframe, around 16k as expected

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   16170 non-null  object
dtypes: object(2)
memory usage: 986.5+ KB


In [155]:
df.to_csv('first_sixteen_thousand_ratings.csv') # let's save these to a csv as well

In [156]:
df_last_part = df[16165:] # create a subset starting near the last non-null value index
df_last_part.head() # double check by printing the first 5 rows

track_lyrics  \
track_id                                                                    
0EDyoVqPdg9AMt8PuDeu9c  Four dark riders, the black demons of Revelati...   
0TEDW3maHntHKBOkkdfPHx  Hi, my name is Siri\nI'm a humanized artificia...   
0mxjKriHsdi8zKiBTWIOrT  Bring the house down\nBring the\n\nIt is our d...   
15avYgGiZCIT8PYtcRH7VU  I knew that it could be a sound of the future ...   
6DHMWFchF9eAEFEM6euZto  Radio? Check, check\nVideo? Check, check\nThis...   

                                    gpt_ratings  
track_id                                         
0EDyoVqPdg9AMt8PuDeu9c  5 2 7 6 4 7 2 1 2 1 2 4  
0TEDW3maHntHKBOkkdfPHx  7 3 8 7 5 8 2 1 1 9 1 1  
0mxjKriHsdi8zKiBTWIOrT  8 6 8 7 5 8 6 4 8 6 4 5  
15avYgGiZCIT8PYtcRH7VU                      NaN  
6DHMWFchF9eAEFEM6euZto                      NaN

In [157]:
# use the same for loop on the new dataframe 
for index, row in df_last_part.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_last_part.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 'not null' only a few times

not null
not null
not null
Getting ratings for I knew that it could be a sound of the f
Getting ratings for Radio? Check, check
Video? Check, check

Getting ratings for We want to see your hands up!
Pe-Pe-Pegb
Getting ratings for Used to call your name
Feel the same way
Getting ratings for If I just let you be
Will you remember m
Getting ratings for You're gonna find me
You're gonna find m
Getting ratings for You're my all you're my all you're my ev
Getting ratings for Yo, I'm in Atlanta, bruh
Hit me back, li
Getting ratings for Let me not, I fear not what you do or wh
Getting ratings for Lavan reunaan haistan hien
Sekamelska hi
Getting ratings for Noir, comme le ciel d'automne la nuit
Co
Getting ratings for I've been staring at a road
I've been st
Getting ratings for ""
"Artillery, I hope you get this messa
Getting ratings for Hold on to the world you've been dreamin
Getting ratings for I keep you away, I keep you away, I keep
Getting ratings for Nem Azahriah a hibás!
Nem ő a hibás!



Getting ratings for Nostalgia’s wisp fades to grey skies
Com
Getting ratings for Caught my heartbeat, reeled me in
Tricke
Getting ratings for 몇분뒤 해뜨는데
난 still in the club
모두 누군가 데리고 
Getting ratings for Girl I can't breath
I need oxygen
When t
Getting ratings for Illustrate like Stan Lee... Kubrick
Colo
Getting ratings for Out!
Never more!
Run like demon
Light!
C
Getting ratings for Effie? Curtis was supposed to--

Love me
Getting ratings for The past is meeting the future
The futur
Getting ratings for "There is absolutely no reason for a rec
Getting ratings for Some people think that
They can just get
Getting ratings for Welcome to the Roaring 2020s!
Roll up, a
Getting ratings for Ba, da‚ ba‚ ba
Just let go
Ba‚ da, ba, b
Getting ratings for Oh, rock and get at me and fight us like
Getting ratings for He was a cool man
He went to downtown ab
Getting ratings for Outlawz, go ahead, in this
No doubt
Deat
Getting ratings for Outlawz, go ahead, in this
No doubt
Deat
Getting ratings for You 

Getting ratings for Feeling like a moth in the night
Always 
Getting ratings for We go in circles, you and me
We say the 
Getting ratings for I'm feeling numb most days, most days
I 
Getting ratings for Once upon a time, I went away
To my safe
Getting ratings for You keep calling me
Follow me on the int
Getting ratings for Vic Vella:
...well
Steve:
Oh yeah?
Vic:

Getting ratings for High tides, good vibes
Didn't take us lo
Getting ratings for So I don't care if we never get richer
I
Getting ratings for I sense there's something wrong
There's 
Getting ratings for I'm happy that I was a waste of time
I'm
Getting ratings for I remember when we started out
Everythin
Getting ratings for Snow falling so beautiful
Just like your
Getting ratings for I told you once, baby
I told you once, b
Getting ratings for And here we are
Dancing in the strobe li
Getting ratings for This is the rythm of my life, the night,
Getting ratings for I get stuck on every line
Trying to find
Getting ratings for If I

Getting ratings for Steppin' side to side
Bodies gently movi
Getting ratings for You're hurtin’ so much
I need you to bre
Getting ratings for Let the, let the, let the feelings take 
Getting ratings for Stairs upon the temple, I climb and I cr
Getting ratings for Reach out and touch faith
Your own perso
Getting ratings for Hell raising, hair raising
I'm ready for
Getting ratings for If you see me gone, it's alright
'Cause 
Getting ratings for Camila Cabello - Real Friends
Big Sean &
Getting ratings for And another one bites the dust
But why c
Getting ratings for Uh, ah
Sock it to me like you want to, o
Getting ratings for Ayoo
Mic check
Ek shoinno ek
Sr101 music
Getting ratings for Moving on the dancefloor
Dancing tonight
Getting ratings for Moving up and down, side to side, like a
Getting ratings for We call it
We-we-we drink it
We call it

Getting ratings for Compro Phoskitos, ah, solo por la sorpre
Getting ratings for Into you
Into you
Into you
Into you
Into
Getting ratings for Majo

Getting ratings for Waiting at the corner where we used to m
Getting ratings for Verso 1 (SD)
Socio yo no tengo tracks
Yo
Getting ratings for I used to think that I wasn't fine enoug
Getting ratings for Bjorn:
My Chieftain father said to me
"M
Getting ratings for Say, R.I.P. to Pimp C, he was the King o
Getting ratings for Vieja
Esta canción la voy a cantar con P
Getting ratings for This is what the kids call hot

-on a CD
Getting ratings for Yo, yo
It seems we meet again
Frequencie
Getting ratings for The beat is engineered around Alan Tew's
Getting ratings for (Y2, is that you?)
(Ayy, Cv, you cooked 
Getting ratings for Yeah over and over and over again
Just l
Getting ratings for Pele bataa dun gaali bakun ga mein boht

Getting ratings for Yeah, well, tell me why we been so dista
Getting ratings for I always feel like
Somebody's watching m
Getting ratings for If I could write you a song to make you 
Getting ratings for Don't know when it started and I don't k
Getting ratings for And 

...

Getting ratings for Yeah, Spyderman and Freeze in full effec
Getting ratings for Yo sé que no necesitas que te hablen de 
Getting ratings for I poured you a glass of wine
And drank i
Getting ratings for Uh-jah
Uh-jah (Daddy)
Uh-jah (Zion & Len
Getting ratings for Comin' over in my direction
So thankful 
Getting ratings for Did a full 180, crazy
Thinking 'bout the
Getting ratings for Ain’t got no riches, ain’t got no money 
Getting ratings for Children grow and women producing
Men go
Getting ratings for Screams break the silence
Waking from th
Getting ratings for Dirty, rotten, filthy, stinkin'...

She'
Getting ratings for It happened the moment, when you were re
Getting ratings for Let it never be said that romance is dea
Getting ratings for I've been going down the wrong kinda roa
Getting ratings for Joey
¿Cómo sucedió? No sé
Si en mis plan
Getting ratings for You weren't the boy I thought I knew
May
Getting ratings for Pero
Yo te deje todo claro
En que habíam
Getting ratings for I lo

Getting ratings for With a purposeful grimace and a terrible
Getting ratings for Alright, stop what you're doin' 'cause I
Getting ratings for Quiero que todos hagamos palmas
No vuelv
Getting ratings for *Sirens*
Ah, shit! Man, them pinche blac
Getting ratings for I wanna dance by water 'neath the Mexica
Getting ratings for Up outta there
Ain't nothin' but a gangs
Getting ratings for Still tippin' on four fours wrapped in f
Getting ratings for D-D-D-, D.O.!
Diesel!
‎iDon!

Ella es es
Getting ratings for Maybe it's nice to be alone in the end
Y
Getting ratings for चाँद पे, चाँद पे
चाँद पे, चाँद पे

चाँद 
Getting ratings for (The truth is, I thought it mattered)
(I
Getting ratings for Feelin' the song, party done, shadows wa
Getting ratings for Breathing you in when I want you out
Fin
Getting ratings for Boy, there you go
You're tellin' me that
Getting ratings for I must be tough
I must behave, I must ke
Getting ratings for Uso pa ba ang harana?
Marahil ikaw ay na
Getting ratings for Down

Getting ratings for Oh it's a long way down
But if you don’t
Getting ratings for I'll always think of you
Inside of my pr
Getting ratings for She want to move to California
She must'
Getting ratings for A bird with the word came to me
The swee
Getting ratings for Wrote another text that I'll never send

Getting ratings for You're my baby, my lover, my lady
All ni
Getting ratings for There is only one for me
You have made 
Getting ratings for Yeah, yeah, yeah, yeah, yeah
Grown-ups, 
Getting ratings for Well, I don't know where they come from 
Getting ratings for Love hurts, love scars
Love wounds and m
Getting ratings for Ooh-ooh
Ah-ah, ah-ah, whoa-oh
Ooh-ooh, o
Getting ratings for Play this record as frequently as possib
Getting ratings for I wanna freek you
I wanna freek you
I wa
Getting ratings for Headbangers in leather
Sparks flyin' in 
Getting ratings for Let's go to the park
I wanna kiss you un
Getting ratings for Cold late night, so long ago
When I was 
Getting ratings for Shawt

Getting ratings for Yeah, you know what, what, what
I'm bout
Getting ratings for Bag lady, you gone hurt your back
Draggi
Getting ratings for Hey, living in a California cage
Y'all t
Getting ratings for Loving can hurt, loving can hurt sometim
Getting ratings for One, two, three let's go!
One, two, thre
Getting ratings for Said papa gon' roll one for me
He gon' g
Getting ratings for You've got to keep moving
You've got to 
Getting ratings for My buddy, my buddy
Wherever I go, he go

Getting ratings for Now let's get down to business, bitches!
Getting ratings for I'll give you the sun, the rain, the moo
Getting ratings for Hahaha
Let the sparks fly
Hahaha

There'
Getting ratings for You got me shook up, shook down, shook o
Getting ratings for Blaze up (Oh yeah!)
World wide, don't st
Getting ratings for It's been a long time (Long time)
We sho
Getting ratings for I wear tight clothing and high heel shoe
Getting ratings for The truth about a roni, she's a sweet li
Getting ratings for Yeah

KeyboardInterrupt: 

In [158]:
df_last_part.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3907 entries, 0EDyoVqPdg9AMt8PuDeu9c to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  3907 non-null   object
 1   gpt_ratings   3627 non-null   object
dtypes: object(2)
memory usage: 220.6+ KB


In [159]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_last_part['gpt_ratings']) # fill the nulls in the larger dataframe
df.info() # check the number of non-nulls in the larger dataframe, around 19k as expected

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   19792 non-null  object
dtypes: object(2)
memory usage: 986.5+ KB


In [160]:
df.to_csv('first_nineteen_thousand_ratings.csv') # let's save these to a csv as well

In [161]:
# use the same for loop on the new dataframe 
for index, row in df_last_part.iterrows():
    if pd.isnull(row['gpt_ratings']):  # Check for null values
        df_last_part.loc[index, 'gpt_ratings'] = get_ratings(row['track_lyrics'])
    else:
        print('not null') # should print 'not null' many times

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
not null
n

Getting ratings for There's something I want to tell you
The
Getting ratings for Yeah, I know you see the drip and you li
Getting ratings for I know I took the path
That you would ne
Getting ratings for 朝焼けの中であなたの寝顔みてると なぜか
信じられないの 幸せすぎて不安になるわ
Getting ratings for (We love you, Tecca)

I got a pack, hit 
Getting ratings for Yeah (yeah)
This song here is called "Go
Getting ratings for Monday morning, saw my darling
Out the w
Getting ratings for I may be crazy
Tired of all those fairy-
Getting ratings for I'm still Pimp C bitch so what the fuck 
Getting ratings for Alright
This one goes out to all the lov
Getting ratings for It never rains in southern California
I'
Getting ratings for So you say you wanna get away
We don't n
Getting ratings for Westside!
Hoo-Bangin' on the transformer
Getting ratings for Asesino de asesinos, como Raid los elimi
Getting ratings for I don't care if you hurt me some more
I 
Getting ratings for Never was a leader
Never had a thing for
Getting ratings for If t

Getting ratings for Now come follow me, come follow me, come
Getting ratings for Come here, baby
You know you drive me up
Getting ratings for Mek dem know
Jenil
Yo, Window
Richie Loo
Getting ratings for Love it, mane

Twenty-five lighters on m
Getting ratings for "Check this out"
"Check this out"
"Ah— a
Getting ratings for Every breath you take and every move you
Getting ratings for I'm so sorry, baby
I never meant to hur
Getting ratings for What we're gonna do now is go back

Ever
Getting ratings for Я, как яблоки на снегу
Лежал, пока меня 
Getting ratings for We built this city
We built this city on
Getting ratings for (Ku ke ti moj ajshe, moj te molla)
(Aman
Getting ratings for Oh
My name is Jahbless
Oya e package, pa
Getting ratings for Mercedes
Mer—, Mer—, Mer—, Mercedes
Do y
Getting ratings for We hope you enjoyed your train ride
From
Getting ratings for You get a shiver in the dark
It's rainin
Getting ratings for Can't you see my rhythms deep inside
Sin
Getting ratings for There

Getting ratings for Yeah, I just can't get enough of your lo
Getting ratings for 12/1
Aya Nakamura - "SMS"
Cordae - "Feel
Getting ratings for Hit me.
All the chronic in the world cou
Getting ratings for Your hand in my hand and my hand in your
Getting ratings for It's more than I can take
Just slowly co
Getting ratings for One, two, three, let's go!

Lil mama, sh
Getting ratings for Uh, uh, uh, uh

Bring it, what?
We right
Getting ratings for Welcome to the land where it just don't 
Getting ratings for Welcome to the uh Southside
No, uh-uh, I


In [162]:
df_last_part.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3907 entries, 0EDyoVqPdg9AMt8PuDeu9c to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  3907 non-null   object
 1   gpt_ratings   3907 non-null   object
dtypes: object(2)
memory usage: 220.6+ KB


In [163]:
df['gpt_ratings'] = df['gpt_ratings'].fillna(df_last_part['gpt_ratings']) # fill the nulls in the larger dataframe
df.info() # check the number of non-nulls in the larger dataframe, all non-null as expected

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   20072 non-null  object
dtypes: object(2)
memory usage: 986.5+ KB


In [164]:
df.tail(20)

track_lyrics  \
track_id                                                                    
1JsbFVFHNIi7kAhlpxDLhV  You let me free but i know am captive alive\nY...   
0DC5wcWwsGTGlBkVsb6PVe  Two feet they come a creepin'\nLike a black ca...   
6uPnJMpmcYw9f8oyQZP4XD  Everybody's saying silly things\nWithout knowi...   
0JufJHXVWc2cQsWXgZMbKV  Quiero llevarte a un lugar donde se vive el am...   
54mCRV3SMDTLlXqeDp0nmv  Nosotros somos del Caribe oite' loco\nSupremo\...   
31H7LPONnW6megZrmnN5th  Ladies and gentlemen\r\nThe moment you've all ...   
1Jgaw4deeHcbldSmKbP5h3  Yeah (ah)\r\nFirm biz, what is, Blackstreet\r\...   
47phWmK3Q9zG3nFiYQv5IT  Yeah\r\nJust like the old times\r\nI know a lo...   
6Ct0xRDiianggXtNh1kWez  Yo, drop it\nI wanna get with you (I wanna)\nS...   
7rzaHTWzsnyz3v9liUNW2I  I've got to get away \r\n\r\nAin't nothin' but...   
5wqB7S73zPUAtdcCvKZflz  Papa just keep me laced up\nIn Ellen Tracy, uh...   
2M4pc3d5VTELAnjCkivkOf  Yeah, I just can't get enough of your love, ba...   
0GBm0i9OlIlxQGx8fCNzoN  12/1\nAya Nakamura - "SMS"\nCordae - "Feel It ...   
4q2RJH99DFckparlsfCpBc  Hit me.\nAll the chronic in the world couldn't...   
4LbO2pzBtVQnHvrYEIwNPO  Your hand in my hand and my hand in your hand\...   
5AiNxLZufMUfR6ADAxxqOe  It's more than I can take\nJust slowly coming ...   
2MzLi4EopILqoDTZuLtIzW  One, two, three, let's go!\n\nLil mama, show m...   
48A3iXuphgaaQ3yoLeV5RJ  Uh, uh, uh, uh\n\nBring it, what?\nWe right he...   
3tQnH83OR5LgMkPqGrnZo5  Welcome to the land where it just don't stop\n...   
4xL5ytWp07oOvYRtcN4ehe  Welcome to the uh Southside\nNo, uh-uh, I said...   

                                    gpt_ratings  
track_id                                         
1JsbFVFHNIi7kAhlpxDLhV  9 6 7 7 5 7 4 5 5 4 4 4  
0DC5wcWwsGTGlBkVsb6PVe  7 5 8 8 6 8 3 2 2 2 2 4  
6uPnJMpmcYw9f8oyQZP4XD  8 7 9 8 7 8 7 5 4 4 4 6  
0JufJHXVWc2cQsWXgZMbKV  8 8 9 8 7 8 8 6 5 4 4 8  
54mCRV3SMDTLlXqeDp0nmv  8 7 8 8 7 8 5 6 4 4 6 7  
31H7LPONnW6megZrmnN5th  6 3 7 5 3 6 2 1 1 1 1 2  
1Jgaw4deeHcbldSmKbP5h3  7 6 8 7 6 8 4 3 4 4 5 6  
47phWmK3Q9zG3nFiYQv5IT  8 6 8 7 6 8 4 4 3 3 4 6  
6Ct0xRDiianggXtNh1kWez  5 2 8 5 2 8 2 2 3 2 2 2  
7rzaHTWzsnyz3v9liUNW2I  7 6 7 7 6 7 6 5 6 5 5 6  
5wqB7S73zPUAtdcCvKZflz  6 4 7 6 5 6 3 4 2 1 2 3  
2M4pc3d5VTELAnjCkivkOf  8 6 8 7 6 8 7 6 3 3 4 6  
0GBm0i9OlIlxQGx8fCNzoN  5 5 6 5 4 6 4 4 3 4 5 6  
4q2RJH99DFckparlsfCpBc  7 5 8 7 6 8 3 3 6 5 4 6  
4LbO2pzBtVQnHvrYEIwNPO  7 5 7 6 5 7 3 3 3 3 3 3  
5AiNxLZufMUfR6ADAxxqOe  8 6 8 7 6 8 5 5 4 4 4 6  
2MzLi4EopILqoDTZuLtIzW  6 3 7 5 4 6 7 4 2 2 3 2  
48A3iXuphgaaQ3yoLeV5RJ  5 3 5 4 3 6 2 1 1 1 2 3  
3tQnH83OR5LgMkPqGrnZo5  6 3 6 5 3 6 4 2 3 2 3 2  
4xL5ytWp07oOvYRtcN4ehe  3 1 3 2 1 3 1 1 1 1 1 1

In [205]:
# df.to_csv('all_ratings.csv') # let's save these to a csv as well

In [289]:
df = pd.read_csv('all_ratings.csv', index_col=0) # re-load
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 20072 entries, 0r7CVbZTWZgbTCYdfa2P31 to 4xL5ytWp07oOvYRtcN4ehe
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   track_lyrics  20072 non-null  object
 1   gpt_ratings   20072 non-null  object
dtypes: object(2)
memory usage: 470.4+ KB


When I tried to separate each rating and store it in its own column, I got an error saying "Columns must be same length as key". Let's see what's going on.

In [290]:
df['ratings_length'] = df['gpt_ratings'].apply(len) # get the length of the objects in gpt_ratings column
df['ratings_length'].unique() # get all the unique ones

array([ 23,  24,  25,  26,  35,  22,  47, 181, 206, 179,  84])

In [291]:
# majority is 23, which means each raiting is a one digit number with one space in between
df['ratings_length'].value_counts() 

ratings_length
23     19986
24        42
25        29
26         7
35         2
22         1
47         1
181        1
206        1
179        1
84         1
Name: count, dtype: int64

In [292]:
df[df['ratings_length']==24] # filter for 24 characters long ratings

track_lyrics  \
track_id                                                                    
7dLOOzJGQnsgqFcflWiEcZ  Only you, only you\n\nWanted to write you some...   
21X8grU7IMAVa2elySGIRR  (Scientist voice:\n"Say, what do you suppose i...   
6sNs67OYo6O7HBVwr0ugl3  You move through my body like an ocean\nDidn’t...   
2L9LE3tQ97iouD4ELWCH8n  The drops of rain they fall all over\nThis awk...   
330sg1eKlLIvWRJCAttThK  Si las miradas mataran\nDesde hace semanas\nEs...   
1HxL3DniLhRd8Qy9ENVRr7  With each day the same as the next\nI rest in ...   
0Psz3az3RIYfJpnsajBT8N  Sou de Nanã, euá, euá, euá, ê\nSou de Nanã, eu...   
1Qz1BjKg0fgwSZQXYgyZR9  Take note of what you're feeling, make every m...   
3aNsRsxKJWI7QdKEbav4e4  O! it is pleasant, with a heart at ease,\n    ...   
3IgTG5T8Mv0a7wBvbc0iNv  The more I look\nI see you in every moment\nFr...   
2P3VCrDzYC9XzS7Bwu5dN3  君の肩　抱くように　都会まちに秋の風\n心まで迷わせて　どこかに連れ去る\n\n僕は１人きり...   
44qXe4KIx8bu9eLtTV1BB8  Something has left my life\nAnd I don't know w...   
21W8a3ihSeIcRjOPn1Lz5F  A menudo me recuerdas a alguien\n\nTu sonrisa ...   
0RJJfHHtI0cSUyCzNUdBEX  Beside a river, deeply cloaked,\na Ceiba's cro...   
3I8Ri6tLa4QA11MMdZywtM  Ah\nOoh\n\nKick the dog when the whistle blows...   
3UTItBKzuk2IOqxVu0C2F8  The music of Louisiana is one of the most vari...   
5DsD9rUwGiiWZxyDPkm48V  I think it's time for me to go now\nI've done ...   
4mgDustRkMhvBTvO0mC8Su  You'll never know what it feels like 'til you'...   
4N4STDrAmiZoVLVFGwDXp3  Camine triste por la vereda\nY me cruce con un...   
4ZhEevPVamfM1HFBCDYbOu  It's a sunny day, no stormy weather\nThere's a...   
1cg5GVCTWza8bQnxM2FHia  azumba. azumba. azumba. azumba.  eek eek eek e...   
21brTVDh5Y3B3mA4z5yyaU  I'm on fire \r\nMy emotions run so deep \r\nYo...   
1Hm7dHnPVarIrxbxh5h8PN  Pequeno Juan (Yeah)\nMr. Worldwide (Yeah!)\nEs...   
7dVPy89Xmj4Ovmn3cqleVt  Our conversation ought to remain\nBetween two ...   
34Ai7jMLLwZdJSGadARhLK  Before I go now\nLook me right in the eye\nAnd...   
6yTZofBlqETycKBEUdsGxp  (Intro)\nAh-one two\nOkay, okay, o-o-o-o-okay\...   
4Yenz5JZZOUiZSeyKY8bDz  Oh yeah!\r\nIn France, a skinny man died of a ...   
1SQrYjoC3yJAIuBiAhdcVp  You been there for me wherever you go\nYou lea...   
3jEBoIiTgxffp0ilDu7CpI  Now that you're right here,\r\nLet me whisper ...   
24Rz7seIzZoUYVlLWIAk0v  If I want you, be my lady\nI'm gon' call you\n...   
6ItLASP9h9ZvU1J9iXEVXS  Too many colors blind\nSo many righteous peopl...   
1345xOev1kyaeqRdeTxiLi  Like a leaf clings to a tree\n\nThe world is w...   
1W5Z5qzqGVqfVLfgo2JdHi  I was down until I got tired and got up\nI was...   
7plNxAMx3m8o2et2UEeCFm  Keine Angst, keine Angst\nAlles wirkt so ander...   
0Mft55GDMuD2rFnrSeFn3U  I just want you here\nLike it was 1941\nPlay t...   
1mEUuGPU7gCcIkwt5QDobg  It's time to go If you don't dig techno\n\nTec...   
3hxOnhD25gQj3giyWCMTEb  Vieja\nEsta canción la voy a cantar con Pablo ...   
00Gu3RMpDW2vO9PjlMVFDL  Don't run away, it's getting colder\nOur heart...   
3UyZtf5BzjEYFJkIiIipoH  Come now, surely we can be friends. I know so ...   
1mG0wSudoIljGvU5KqVLj8  I dreamed I saw Jesus last night\nSeated on a ...   
2GHNZvjA57wLRl4FVk0MhS  That's what I'm talking about\nThat's what I'm...   
1fDsrQ23eTAVFElUMaf38X  A long, long time ago\nI can still remember ho...   

                                     gpt_ratings  ratings_length  
track_id                                                          
7dLOOzJGQnsgqFcflWiEcZ  8 6 8 7 6 8 6 4 4 4 5 6               24  
21X8grU7IMAVa2elySGIRR  7 5 8 8 7 8 3 2 6 4 5 3               24  
6sNs67OYo6O7HBVwr0ugl3  8 7 8 8 7 8 6 5 4 4 5 6               24  
2L9LE3tQ97iouD4ELWCH8n  8 6 8 7 6 8 4 4 4 4 5 5               24  
330sg1eKlLIvWRJCAttThK  7 6 7 7 8 7 5 6 4 4 5 6               24  
1HxL3DniLhRd8Qy9ENVRr7  8 7 8 8 7 8 6 5 4 4 5 6               24  
0Psz3az3RIYfJpnsajBT8N  10 8 9 9 9 8 8 6 6 6 6 6              24  
1Qz1BjKg0fgwSZQXYgyZR9  9 8 9 8 7 9 8 7 6 4 5 8               24  
3a

In [294]:
# let's check 25 characters long ratings
df[df['ratings_length']==25]

track_lyrics  \
track_id                                                                    
328F2sC7uw6wdkWLggOAQ2  I was feeling nostalgic\nFor the days when my ...   
6xPVnZ5WcK9sh9FyYIkiW3  Here is a list of the cast from Sesame Street....   
3AHqaOkEFKZ6zEHdiplIv7  Billie Eilish - everything i wanted\nKhalid - ...   
38rSSynmRf2kxslXKS50u8  Me encaminé, y dediqué\nA inventarme, que me a...   
0bqfNDZvqXB10fUKSfj6mY  Tres mas y once meses\nPa' llegar hasta el fin...   
0TD0ydYJuFPEaqshquDEpw  You wouldn't dare\nWell you've never left home...   
71SidvkT6LCBHRZI858TsQ  She knows this feeling all too well\nShe feels...   
2nH0gsXkSo8hsMv992jbTm  Something about you escapes me\nI've lost my c...   
2Xo3rLHjXfdb4avN68aQyi  Katy Perry - Harleys In Hawaii\nBTS - Make It ...   
62r62ArmWq38cu6QCVgyTc  Order, huh\r\nYo, we at war\r\nWe at war with ...   
69eXHDgEEQ6itzt03E7fKz  Katy Perry - Harleys In Hawaii\nBTS - Make It ...   
0CLhMOVhX6TaPpugYkEsge  Taylor Swift - The Man\nCharlie Puth - I Warne...   
3mgfxXdvKRLlo2X1mmp10j  Billie Eilish - everything i wanted\nKhalid - ...   
7MooGz4ZPE4bNxjFegR6Jx  Let me run with you tonight\nI'll take you on ...   
7nnWIPM5hwE3DaUBkvOIpy  Sometimes, I feel the fear of uncertainty stin...   
61US1T9Eq54jUoeMUcchQJ  When I saw you in Verona\r\nYou sat down I mov...   
7s41ZGjQB5Ur8T0fQlk5uM  Quiero ver tu risa todo el día\nEscuchar la me...   
6gyAv8ubr2vaTRdn5bftyb  This is my rebel yell\n\nWhat about freedom?\n...   
00PXizG9xlUNINeqADlh96  Pequeno Juan (Yeah)\nMr. Worldwide (Yeah!)\nEs...   
4OBZT9EnhYIV17t4pGw7ig  mattdeguia - drive slow 5.0\nJLZ - Ela vai sub...   
71fcC7BuScQCY40HIiMyal  I'm so confused\nAnd I think I'm gonna cry ton...   
51cMgiP4rh7RU58hsLJjDR  Following this feeling with you\nI keep on...\...   
5e60CEqPnkrex3BI9tWnpU  Old hollow eyes\nGot no ties\nWalking by the l...   
1kHxfbiZ6HOagkTTrWbICH  Birds flying high, you know how I feel\nSun in...   
7dFikRPQuLFz4PdCw4ZvCy  When the valley couldn't hold me, they throw m...   
6FFGiEHSF7oAMAzhqWxKs7  Un paese vuol dire non essere soli\nAvere gli ...   
3upKMVrJE7lq34tSqWIPkJ  Je te vois dans mes rêves. mon amour\nTu reste...   
45cOIUfSBmCvDBofEFO4e7  Oh, come on in\nJust give me the sunshine\nOh ...   
2YWjW3wwQIBLNhxWKBQd16  Drake - One Dance feat. Kyla & WizKid\nMike Po...   

                                      gpt_ratings  ratings_length  
track_id                                                           
328F2sC7uw6wdkWLggOAQ2  8 7 8 7 6 8 4 4 4 4 5 5 7              25  
6xPVnZ5WcK9sh9FyYIkiW3  8 6 7 6 5 8 6 4 4 4 5 5 7              25  
3AHqaOkEFKZ6zEHdiplIv7  6 5 7 6 6 6 5 4 4 4 5 5 6              25  
38rSSynmRf2kxslXKS50u8  7 6 7 7 6 7 6 6 5 4 5 6 7              25  
0bqfNDZvqXB10fUKSfj6mY  7 6 7 7 6 7 6 4 4 4 5 5 6              25  
0TD0ydYJuFPEaqshquDEpw  8 7 8 8 7 8 6 5 4 4 5 6 7              25  
71SidvkT6LCBHRZI858TsQ  9 8 9 8 7 9 8 7 6 4 5 8 8              25  
2nH0gsXkSo8hsMv992jbTm  8 7 9 8 7 8 6 5 4 4 5 6 7              25  
2Xo3rLHjXfdb4avN68aQyi  5 4 6 5 4 4 6 5 4 4 5 5 4              25  
62r62ArmWq38cu6QCVgyTc  7 8 9 8 7 8 3 5 6 4 5 8 7              25  
69eXHDgEEQ6itzt03E7fKz  5 5 6 5 4 5 6 5 4 4 5 5 4              25  
0CLhMOVhX6TaPpugYkEsge  6 5 7 6 5 6 7 4 4 4 5 6 5              25  
3mgfxXdvKRLlo2X1mmp10j  6 5 7 6 5 6 5 4 4 4 5 6 5              25  
7MooGz4ZPE4bNxjFegR6Jx  8 7 8 8 7 8 6 4 4 4 5 5 5              25  
7nnWIPM5hwE3DaUBkvOIpy  9 8 9 8 7 9 7 4 4 4 5 5 7              25  
61US1T9Eq54jUoeMUcchQJ  8 7 8 8 7 8 7 6 4 4 5 6 7              25  
7s41ZGjQB5Ur8T0fQlk5uM  9 8 9 8 7 8 7 7 6 4 5 6 7              25  
6gyAv8ubr2vaTRdn5bftyb  9 8 9 8 7 9 8 7 6 4 5 6 8              25  
00PXizG9xlUNINeqADlh96  7 6 8 7 6 8 7 8 6 4 5 6 7              25  
4OBZT9EnhYIV17t4pGw7ig  6 5 5 5 4 6 5 4 4 4 5 6 5              25  
71fcC7BuScQCY40HIiMyal  7 6 7 7 6 7 5 4 4 4 5 6 7              25  
51cMgiP4rh7RU58hsLJjDR  7 6 7 6 5 7 6 6 4 4 5 6 7              25  
5e60CEqPnkrex3BI9tWnpU  7 5 8 7 6 8 4 4 6

Some of these are 13 scores instead of 12 (same as the number of criteria). I will deal with these later.

In [295]:
# similarly, those that are 26 characters in length are also 12 scores but 3 of them are 10
df[df['ratings_length']==26]

track_lyrics  \
track_id                                                                    
4Vdbb7QK3czCJVdfxOBbCZ  Without you, without you, without you\nWithout...   
64Ret7Tf2M8pDE4aqbW2tX  "Fuckin' coward! Get your ass out of that tren...   
6Ad5TdlevXBRsOsYhCbgb2  Oh, oh my, my, my, my\nOh, oh my, my, my, my\n...   
7a5OUYOGtWSHKlsZz4n3QL  Come close\nCome close\nCome close\n\nCome clo...   
3mdyi1i0w7bfe72a2GX4JX  Keep it real, keepin' it real\nKeep it real, k...   
1UTXQrmAL4oladIwc1PWSh  Forever is a metaphor for now\nForever is a me...   
2eGjOUaoGtr0BwD9Uw6sCl  Get up, no more\nGet up, no more\nGet up, no m...   

                                       gpt_ratings  ratings_length  
track_id                                                            
4Vdbb7QK3czCJVdfxOBbCZ  10 5 10 5 5 10 5 5 5 5 5 5              26  
64Ret7Tf2M8pDE4aqbW2tX  7 8 9 8 9 9 2 1 1 10 10 10              26  
6Ad5TdlevXBRsOsYhCbgb2  10 1 10 1 1 1 10 1 1 1 1 1              26  
7a5OUYOGtWSHKlsZz4n3QL  10 1 10 1 1 10 1 1 1 1 1 1              26  
3mdyi1i0w7bfe72a2GX4JX  10 1 10 1 1 10 1 1 1 1 1 1              26  
1UTXQrmAL4oladIwc1PWSh  10 5 10 7 9 10 6 6 5 5 5 5              26  
2eGjOUaoGtr0BwD9Uw6sCl  10 1 10 2 1 10 1 1 1 1 1 1              26

I will handle those above separately while splitting to create columns for each score later. Let's move on to other lengths.

In [296]:
df[df['ratings_length']==35] # filter the data for 35 characters-long ratings

track_lyrics  \
track_id                                                                    
4n6z0yh2ZpoGh0RNyGVu52  (Instrumental)\n\nOne day, one day at a time\n...   
1wJUs2lr1drNrxMnJ0xAhE  * = letra incompleta.01/11Dalex - Hola (Remix)...   

                                                gpt_ratings  ratings_length  
track_id                                                                     
4n6z0yh2ZpoGh0RNyGVu52  N/A N/A N/A N/A N/A N/A 6 4 4 4 4 4              35  
1wJUs2lr1drNrxMnJ0xAhE  N/A N/A N/A N/A N/A N/A 5 5 3 3 4 5              35

In [297]:
# first one is an intrumental piece with not many words in the lyrics
df.loc['4n6z0yh2ZpoGh0RNyGVu52', 'track_lyrics'] 

"(Instrumental)\n\nOne day, one day at a time\nOne day, one day at a time\nOne day, one day at a time\nOne day, one day at a time\n\n(Instrumental)\n\nTime's passing by, right behind you\nTime's passing by, right behind you\n\n(Instrumental)178"

In [298]:
df.loc['1wJUs2lr1drNrxMnJ0xAhE', 'track_lyrics'] # the second one is a playlist!

'* = letra incompleta.01/11Dalex - Hola (Remix) Ft. Chencho Corleone Lenny Tavarez Y Juhn\nDarkiel - Gata Perversa\nFeid, Maluma & Sky - Fresh Kerias\nJona Alk — Blanco\nResidente - Pecador\nPablo Chill-E - Amigos Muertos Ft. La Kikada y El FechoRd\nYera - Camellando (feat. Lalo Ebratt)\nYera - Boca Linda\nYera - Todita Completa\nYera - Corazón Roto02/11* Chris Wandell - Adelanto\nJona Alk — Talismán ft. Magoner03/11Jona Alk — Rabia y Miel ft. HippyMigué05/11Lérica & Juan Magán - Fuera De Mí06/11Tracy McGrady - El Que No Salta Es Paco ft. El Futuro Fuera De Orbita07/11Gigolo & La Exce - Vulnerable\nBaby Rasta & Gringo - Evidencia\nOzuna - Hasta Que Salga El Sol\nROSALÍA - A Palé\nOmar Koonze - Me Quedé Conmigo08/11Cardellino - Siento por Ciento (Remix) ft. Tássia Reis\nJona Alk — XXXXXXXX09/1110/11Berner - No Borders (feat. Eladio Carrión)\nJona Alk — TR1ST311/11Jona Alk —  🐸 | Grnll\nMicro TDH & Lenny Tavárez - Demasiado Tarde\nMiky Woodz - No Le Bajé (Como En Los Viejos Tiempos)12/11

This is great news! The model recognized playlists that was left over from the cleaning and did not score them. Let's drop both.

In [299]:
df = df[df['ratings_length']!=35] # filter out 35 character long ratings
df['ratings_length'].unique() # check that they are gone

array([ 23,  24,  25,  26,  22,  47, 181, 206, 179,  84])

Let's move on to 22.

In [300]:
df[df['ratings_length']==22] # filter the data for 22 characters-long ratings

track_lyrics  \
track_id                                                                    
4CF0ypdrYDSEtAczdwrQwo  Pink and blue were dancing\r\nEmpty floor, sha...   

                                   gpt_ratings  ratings_length  
track_id                                                        
4CF0ypdrYDSEtAczdwrQwo  8 6 7 8 7 8 7 6 5 5 6               22

Let's drop this as well since there are 11 ratings here instead of 12.

In [301]:
df = df[df['ratings_length']!=22] # filter out 22 character long ratings
df['ratings_length'].unique() # check that they are gone

array([ 23,  24,  25,  26,  47, 181, 206, 179,  84])

Let's move on to 47.

In [302]:
df[df['ratings_length']==47] # filter the data for 47 characters-long ratings

track_lyrics  \
track_id                                                                    
5TVDnNLRq8ABVgfVqVqtsQ  * = letra incompleta.\n01/04\nFeid & Icon — PU...   

                                                            gpt_ratings  \
track_id                                                                  
5TVDnNLRq8ABVgfVqVqtsQ  N/A N/A N/A N/A N/A N/A N/A N/A N/A N/A N/A N/A   

                        ratings_length  
track_id                                
5TVDnNLRq8ABVgfVqVqtsQ              47

All the scores are N/A. This is another playlist. Let's drop this too.

In [303]:
df = df[df['ratings_length']!=47] # filter out 47 character long ratings
df['ratings_length'].unique() # check that they are gone

array([ 23,  24,  25,  26, 181, 206, 179,  84])

Let's move on to 181.

In [304]:
df[df['ratings_length']==181] # filter the data for 181 characters-long ratings

track_lyrics  \
track_id                                                                    
03rZMTTFsdkZgdm3Z3hOwh  * = letra incompleta.01/08El Cadiz - Te Recuer...   

                                                              gpt_ratings  \
track_id                                                                    
03rZMTTFsdkZgdm3Z3hOwh  I'm sorry, but I cannot provide ratings for a ...   

                        ratings_length  
track_id                                
03rZMTTFsdkZgdm3Z3hOwh             181

In [305]:
df.loc['03rZMTTFsdkZgdm3Z3hOwh', 'gpt_ratings'] # get the text in the ratings

"I'm sorry, but I cannot provide ratings for a list of song titles and artists. If you have specific song lyrics you'd like me to rate, please provide them, and I'd be happy to help."

We can see that the lyrics have the same beginning as the playlists before that the model gave scores of N/A. Let's drop this one too.

In [306]:
df = df[df['ratings_length']!=181] # filter out 181 character long ratings
df['ratings_length'].unique() # check that they are gone

array([ 23,  24,  25,  26, 206, 179,  84])

Let's move on to 206.

In [307]:
df[df['ratings_length']==206]  # filter the data for 206 characters-long ratings

track_lyrics  \
track_id                                                                    
3asvHT081n6YXopu6wrTiH  * = letra incompleta.01/05Mozart La Para — 12 ...   

                                                              gpt_ratings  \
track_id                                                                    
3asvHT081n6YXopu6wrTiH  I'm sorry, I cannot provide ratings for the ly...   

                        ratings_length  
track_id                                
3asvHT081n6YXopu6wrTiH             206

In [308]:
df.loc['3asvHT081n6YXopu6wrTiH', 'gpt_ratings'] # get the text in the ratings

"I'm sorry, I cannot provide ratings for the lyrics you provided as they are in Spanish and not in a format that can be analyzed for the requested criteria. If you have any other English lyrics or text you'd"

In [309]:
df.loc['3asvHT081n6YXopu6wrTiH', 'track_lyrics'][:200] # get the first 200 characters of text in the lyrics

'* = letra incompleta.01/05Mozart La Para — 12 A 12\nAkapellah — Como Mario\nAmenazzy — Especial ft. Salim\nLa Melodía Perfecta - Buum Buum02/05*Amarion — Me Compré Un Full (Amarion Version)\nDon Omar — Ho'

This is a Spanish playlist. Let's drop this too.

In [310]:
df = df[df['ratings_length']!=206] # filter out 206 character long ratings
df['ratings_length'].unique() # check that they are gone

array([ 23,  24,  25,  26, 179,  84])

Let's move on to 179.

In [311]:
df[df['ratings_length']==179] # filter the data for 179 characters-long ratings

track_lyrics  \
track_id                                                                    
1ZGNIcjuRJLK7ewAOM3ZU8  * = letra incompleta.01/08El Cadiz - Te Recuer...   

                                                              gpt_ratings  \
track_id                                                                    
1ZGNIcjuRJLK7ewAOM3ZU8  I'm sorry, but I cannot provide ratings for a ...   

                        ratings_length  
track_id                                
1ZGNIcjuRJLK7ewAOM3ZU8             179

The beginning is the same as other playlists. Let's drop it.

In [312]:
df = df[df['ratings_length']!=179] # filter out 179 character long ratings
df['ratings_length'].unique() # check that they are gone

array([23, 24, 25, 26, 84])

Lastly, let's check 84.

In [313]:
df[df['ratings_length']==84] # filter the data for 84 characters-long ratings

track_lyrics  \
track_id                                                                    
3c2noI6hwdH2YoETIriUbX  We haven't lyrics of this song. Please, add\tt...   

                                                              gpt_ratings  \
track_id                                                                    
3c2noI6hwdH2YoETIriUbX  Clear: 8\nRelatable: 7\nMemorable: 8\nEngaging...   

                        ratings_length  
track_id                                
3c2noI6hwdH2YoETIriUbX              84

In [314]:
df.loc['3c2noI6hwdH2YoETIriUbX', 'gpt_ratings'] # the reply is incomplete since the model tried to also name the criteria

'Clear: 8\nRelatable: 7\nMemorable: 8\nEngaging: 7\nSymbolic: 6\nLyrical: 8\nHappy: 6\nSurpr'

In [315]:
df.loc['3c2noI6hwdH2YoETIriUbX', 'track_lyrics'] # the lyrics seems to be missing as well

'We haven\'t lyrics of this song. Please, add\tthese lyrics for other users. Use "Correct". Thanks to you.'

Let's drop this row as well.

In [316]:
df = df[df['ratings_length']!=84] # filter out 84 character long ratings
df['ratings_length'].unique() # check that they are gone

array([23, 24, 25, 26])

I want to also check that we do not have any other lyrics with the string "We haven't lyrics of this song."

In [317]:
# create a dataframe with the lyrics containing this string
no_lyrics_df = df['track_lyrics'].str.contains("We haven't lyrics of this song.") 
no_lyrics_df.value_counts() # check if there are any True values 

track_lyrics
False    20064
Name: count, dtype: int64

Now I will check whether all the remaining gpt_ratings values are 12 scores when split.

In [318]:
# testing my method
ex = ' 1 9 3 5 10 7 '
ex.strip().split()

['1', '9', '3', '5', '10', '7']

In [319]:
# define a function to get the count of ratings
def rating_counter(text):
    count = len(text.strip().split())
    return count

In [320]:
df['rating_counts'] = df['gpt_ratings'].apply(rating_counter) # apply the function and create a new column
df[df['rating_counts']!=12].head()   

track_lyrics  \
track_id                                                                    
328F2sC7uw6wdkWLggOAQ2  I was feeling nostalgic\nFor the days when my ...   
6xPVnZ5WcK9sh9FyYIkiW3  Here is a list of the cast from Sesame Street....   
3AHqaOkEFKZ6zEHdiplIv7  Billie Eilish - everything i wanted\nKhalid - ...   
38rSSynmRf2kxslXKS50u8  Me encaminé, y dediqué\nA inventarme, que me a...   
0bqfNDZvqXB10fUKSfj6mY  Tres mas y once meses\nPa' llegar hasta el fin...   

                                      gpt_ratings  ratings_length  \
track_id                                                            
328F2sC7uw6wdkWLggOAQ2  8 7 8 7 6 8 4 4 4 4 5 5 7              25   
6xPVnZ5WcK9sh9FyYIkiW3  8 6 7 6 5 8 6 4 4 4 5 5 7              25   
3AHqaOkEFKZ6zEHdiplIv7  6 5 7 6 6 6 5 4 4 4 5 5 6              25   
38rSSynmRf2kxslXKS50u8  7 6 7 7 6 7 6 6 5 4 5 6 7              25   
0bqfNDZvqXB10fUKSfj6mY  7 6 7 7 6 7 6 4 4 4 5 5 6              25   

                        rating_counts  
track_id                               
328F2sC7uw6wdkWLggOAQ2             13  
6xPVnZ5WcK9sh9FyYIkiW3             13  
3AHqaOkEFKZ6zEHdiplIv7             13  
38rSSynmRf2kxslXKS50u8             13  
0bqfNDZvqXB10fUKSfj6mY             13

In [322]:
# let's only keep the rows with the correct number of ratings
df = df[df['rating_counts']==12]
df.shape

(20037, 4)

In [323]:
# create a copy
df1 = df.copy()

# create a column for each score
df1[['Clear', 'Relatable', 'Memorable', 'Engaging', 'Symbolic', 'Lyrical', 'Happy', 'Surprised', 
    'Fearful', 'Angry', 'Disgusted', 'Sad']] = df1['gpt_ratings'].str.strip().str.split(' ', expand=True) 

# check the first five rows
df1.head()

track_lyrics  \
track_id                                                                    
0r7CVbZTWZgbTCYdfa2P31  Here's to the ones that we got\nCheers to the ...   
1z1Hg7Vb0AhHDiEmnDE79l  Summertime and I'm caught in the feeling\nGett...   
75FpbthrwQmzHlBJLuGdC7  Two kids with their hearts on fire\nWho's gonn...   
1e8PAfcKUYoKkxPhrHqw4x  I'm going under and this time I fear there’s n...   
7fvUMiyapMsRRxr07cU8Ef  L.A. on a Saturday night in the summer\nSundow...   

                                    gpt_ratings  ratings_length  \
track_id                                                          
0r7CVbZTWZgbTCYdfa2P31  9 8 9 8 7 9 7 6 5 4 5 8              23   
1z1Hg7Vb0AhHDiEmnDE79l  8 6 8 7 5 8 4 6 5 4 5 7              23   
75FpbthrwQmzHlBJLuGdC7  9 8 9 8 7 9 8 6 5 4 5 8              23   
1e8PAfcKUYoKkxPhrHqw4x  9 8 9 8 7 9 3 5 2 2 3 9              23   
7fvUMiyapMsRRxr07cU8Ef  9 8 9 8 7 9 6 4 3 3 4 7              23   

                        rating_counts Clear Relatable Memorable Engaging  \
track_id                                                                   
0r7CVbZTWZgbTCYdfa2P31             12     9         8         9        8   
1z1Hg7Vb0AhHDiEmnDE79l             12     8         6         8        7   
75FpbthrwQmzHlBJLuGdC7             12     9         8         9        8   
1e8PAfcKUYoKkxPhrHqw4x             12     9         8         9        8   
7fvUMiyapMsRRxr07cU8Ef             12     9         8         9        8   

                       Symbolic Lyrical Happy Surprised Fearful Angry  \
track_id                                                                
0r7CVbZTWZgbTCYdfa2P31        7       9     7         6       5     4   
1z1Hg7Vb0AhHDiEmnDE79l        5       8     4         6       5     4   
75FpbthrwQmzHlBJLuGdC7        7       9     8         6       5     4   
1e8PAfcKUYoKkxPhrHqw4x        7       9     3         5       2     2   
7fvUMiyapMsRRxr07cU8Ef        7       9     6         4       3     3   

                       Disgusted Sad  
track_id                              
0r7CVbZTWZgbTCYdfa2P31         5   8  
1z1Hg7Vb0AhHDiEmnDE79l         5   7  
75FpbthrwQmzHlBJLuGdC7         5   8  
1e8PAfcKUYoKkxPhrHqw4x         3   9  
7fvUMiyapMsRRxr07cU8Ef         4   7

In [326]:
df1.columns

Index(['track_lyrics', 'gpt_ratings', 'ratings_length', 'rating_counts',
       'Clear', 'Relatable', 'Memorable', 'Engaging', 'Symbolic', 'Lyrical',
       'Happy', 'Surprised', 'Fearful', 'Angry', 'Disgusted', 'Sad'],
      dtype='object')

In [340]:
criteria_cols = ['Clear', 'Relatable', 'Memorable', 'Engaging', 'Symbolic', 'Lyrical',
       'Happy', 'Surprised', 'Fearful', 'Angry', 'Disgusted', 'Sad']

not_digits = []
different_digits = []

for index, row in df1[criteria_cols].iterrows(): # iterrate over the dataframe with criteria columns
    if not row[col].isdigit(): # if the rating is not castable to digit
        not_digits.append(index)
    elif int(row[col]) > 10 or int(row[col]) <1: # if the rating changed to integer is bigger than 10 or smaller than 0
        different_digits.append(index)

different_digits, not_digits # get the lists of indices

(['57ma8uG5b7nvK1ZjiZXH0f'], [])

In [339]:
df1.loc['57ma8uG5b7nvK1ZjiZXH0f'] # get the row with this index

track_lyrics      05/01\nbarekprzestań - MIŁO - 2/13\nbryska - b...
gpt_ratings                                 0 0 0 0 0 0 0 0 0 0 0 0
ratings_length                                                   23
rating_counts                                                    12
Clear                                                             0
Relatable                                                         0
Memorable                                                         0
Engaging                                                          0
Symbolic                                                          0
Lyrical                                                           0
Happy                                                             0
Surprised                                                         0
Fearful                                                           0
Angry                                                             0
Disgusted                                       

The model (gpt 3.5 turbo) was not supposed to return a 0 score but it did not like the playlist. Great! Let's drop this one as well.

In [344]:
df1.shape

(20037, 16)

In [345]:
df1 = df1.drop('57ma8uG5b7nvK1ZjiZXH0f') # drop the row with this index
df1.shape[0] # should be 20036

20036

In [346]:
df1.to_csv('../datasets/all_ratings_cleaned.csv') # save this to a csv

I actully want to check the very low Lyrical scores before finalizing.

In [363]:
df1 = pd.read_csv('../datasets/all_ratings_cleaned.csv', index_col=0) # load the data

In [364]:
df1['Lyrical'].value_counts() # let's see the distribution of Lyrical scores

Lyrical
8     9261
9     4036
7     2663
6     2275
5      717
3      345
2      311
4      272
1      150
10       6
Name: count, dtype: int64

In [365]:
df1[df1['Lyrical']==1] # let's see those that received 1

track_lyrics  \
track_id                                                                    
2DSDxFmWjyoKmCamYexX4b  Free For All Match\nBilly Gunn defeats Flash F...   
6zdFOrqnrLzd8r99ZnMJSC  Wow, qué huevo\n\nLa gallina turuleca ha puest...   
2U4tbK3U9DFdZvhLNagF5V  Stack It Up (feat. A Boogie wit da Hoodie)\nLi...   
7lWUJpax919G4JdaFEVmCy  2017 - Present: Rainbow\nAwards & Accomplishme...   
17tDv8WA8IhqE8qzuQn707  2017 - Present: Rainbow\nAwards & Accomplishme...   
...                                                                   ...   
4P7VFiaZb3xrXoqGwZXC3J  Oww! Hahahaha\nUh-huh\nNo homo (Young Mula, ba...   
3qPXWPkEZgUhUgPifbE99z  Sometimes the bomb might explode without any w...   
4Ijr3J0lnLCGZvpXBiqCjU  (You, you, you, you...)\n(You, you, you...)\n(...   
4Q6ZUid2qqoxX3GTlBLCCP  Let's go\nLet's go\n\nLet's go\nPut your let's...   
3utCCAlvSP0yRCrqq0Wrpp  TUTUTUTUTUTUTU\nTUTUTUTUTUTUTU\nTUTUTUTUTUTUTU...   

                                    gpt_ratings  ratings_length  \
track_id                                                          
2DSDxFmWjyoKmCamYexX4b  1 1 2 1 1 1 1 1 1 1 1 1              23   
6zdFOrqnrLzd8r99ZnMJSC  7 2 7 4 1 1 1 1 1 1 1 1              23   
2U4tbK3U9DFdZvhLNagF5V  1 1 1 1 1 1 1 1 1 1 1 1              23   
7lWUJpax919G4JdaFEVmCy  1 1 1 1 1 1 1 1 1 1 1 1              23   
17tDv8WA8IhqE8qzuQn707  1 1 1 1 1 1 1 1 1 1 1 1              23   
...                                         ...             ...   
4P7VFiaZb3xrXoqGwZXC3J  3 1 1 1 1 1 1 1 1 1 1 1              23   
3qPXWPkEZgUhUgPifbE99z  1 1 1 1 1 1 6 1 1 1 1 1              23   
4Ijr3J0lnLCGZvpXBiqCjU  1 1 2 1 1 1 1 1 1 1 1 1              23   
4Q6ZUid2qqoxX3GTlBLCCP  3 1 1 1 1 1 1 1 1 1 1 1              23   
3utCCAlvSP0yRCrqq0Wrpp  1 1 1 1 1 1 1 1 1 1 1 1              23   

                        rating_counts  Clear  Relatable  Memorable  Engaging  \
track_id                                                                       
2DSDxFmWjyoKmCamYexX4b             12      1          1          2         1   
6zdFOrqnrLzd8r99ZnMJSC             12      7          2          7         4   
2U4tbK3U9DFdZvhLNagF5V             12      1          1          1         1   
7lWUJpax919G4JdaFEVmCy             12      1          1          1         1   
17tDv8WA8IhqE8qzuQn707             12      1          1          1         1   
...                               ...    ...        ...        ...       ...   
4P7VFiaZb3xrXoqGwZXC3J             12      3          1          1         1   
3qPXWPkEZgUhUgPifbE99z             12      1          1          1         1   
4Ijr3J0lnLCGZvpXBiqCjU             12      1          1          2         1   
4Q6ZUid2qqoxX3GTlBLCCP             12      3          1          1         1   
3utCCAlvSP0yRCrqq0Wrpp             12      1          1          1         1   

                        Symbolic  Lyrical  Happy  Surprised  Fearful  Angry  \
track_id                                                                      
2DSDxFmWjyoKmCamYexX4b         1        1      1          1        1      1   
6zdFOrqnrLzd8r99ZnMJSC         1        1      1          1        1      1   
2U4tbK3U9DFdZvhLNagF5V         1        1      1          1        1      1   
7lWUJpax919G4JdaFEVmCy         1        1      1          1        1      1   
17tDv8WA8IhqE8qzuQn707         1        1      1          1        1      1   
...                          ...      ...    ...        ...      ...    ...   
4P7VFiaZb3xrXoqGwZXC3J         1        1      1          1        1      1   
3qPXWPkEZgUhUgPifbE99z         1        1      6          1        1      1   
4Ijr3J0lnLCGZvpXBiqCjU         1        1      1          1        1      1   
4Q6ZUid2qqoxX3GTlBLCCP         1        1      1          1        1      1   
3utCCAlvSP0yRCrqq0Wrpp         1        1      1          1        1      1   

                        Disgusted  Sad  
track_id                                
2DSDxFmWjyoKmCamYexX4b          1   

In [366]:
low_lyrical_df = df1[df1['Lyrical']==1]

for index, row in low_lyrical_df.iterrows(): # let's print the lyrics
    print(index)
    print(row['track_lyrics'])
    print("\n ------- \n")

2DSDxFmWjyoKmCamYexX4b
Free For All Match
Billy Gunn defeats Flash Funk (7:05)

Four Way Elimination Tag Team Match
The Headbangers (Mosh and Thrasher) defeat Doug Furnas and Philip LaFon and The Godwinns (Henry O. Godwinn and Phineas I. Godwinn) (w/Hillbilly Jim) and The New Blackjacks (Blackjack Bradshaw and Blackjack Windham) (10:39)
- The New Blackjacks were disqualified (4:37)
- Furnas and LaFon were counted out (5:00)
- Mosh pinned Phineas (10:39)

WWF Intercontinental Title Match
Rocky Maivia (c) defeats The Sultan (w/Bob Backlund and The Iron Sheik) (9:45)

Singles Match
Hunter Hearst Helmsley (w/Chyna) defeats Goldust (w/Marlena) (14:28)

WWF World Tag Team Title Match
Owen Hart and The British Bulldog (c) vs. Mankind and Vader (w/Paul Bearer) - Double Count Out (16:08)

No Holds Barred Submission Match (Special Referee: Ken Shamrock)
Bret Hart defeats Steve Austin by referee's decision (22:05)

Six Man Tag Team Chicago Street Fight
Ahmed Johnson and The Legion Of Doom (Road W

The following are non-lyric text, mostly playlists. Let's drop them.

In [368]:
idx_to_drop = ['2DSDxFmWjyoKmCamYexX4b', '2U4tbK3U9DFdZvhLNagF5V', '7lWUJpax919G4JdaFEVmCy', '17tDv8WA8IhqE8qzuQn707',
          '1afuAgWlDOD48Ue3B3XjJu', '2x0RZdkZcD8QRI53XT4GI5', '0x6rgzl1TnIBBrQ5Gljb4A', '54l9GJGQ1UCFKe2tzt1Vxt',
          '2xeiAqqHWYXQMWk6s2aQdw', '6iRrlcfTyXneYrMmq4ARkl', '4E6KKBjrsR5lu4mHPCVPfs', '4OocfNloIRk77ncIKBdYwb',
          '434qhYDxNYCvwimHtlSNvF', '1BCfh9P3b9ghCYrt3N5Bkp', '6MHOg9xiYC2gj8zcASaLUo', '1YwNlWLf8auhazSQUDQLFU',
          '1Ui4pQVNf9qpwk6mUfiR1A', '51Qo4o1rz2FJ5h0ie2Okjt', '02zyl88XvRAQdwbzLQui8y', '3rMqitYF1U4IHqEQjWhmJP',
          '3xq3EhulVamWqQD0TW7wok', '5F2lWCeBZMxpo6SG1Q3PlL', '2ktoFujjJtantyMoVdBJlX', '0gwq583qFgPczMTFBCB9wu',
          '25xw3RYpFrMkelcojQmhYT', '2izRAdFIQ2ccslSDxO4wp7', '5HoC9hffOsN30JKLU6chQF', '3G3dqYplCvbvv53HkEdZKn',
               '7Eso5mURNFprb5PmhOXDlf', '5IgIor9wnFdCgA1Pc0Xeu4', '5B6sw8Wn9YzGcMgZWDYzyT', '50LC039wMtdkPSi7Bbani1',
          '0cWaeIRKpvONSfktDzK4fN', '6PYnUsNEpYC7A4BS2sjw3L', '5pAbCxt9e3f81lOmjIXwzd', '1xU2QZ40MY4Ex2pfczZa9U',
          '3XKIUb7HzIF1Vu9usunMzc', '72vclXWvJtkFgALSfuX44I', '0bzYxcZv8NUmIYUu5JSQ1j', '2xLBfyAOFlBiuzdIh97FqO',
          '7nV3aBATIajtwj9FK5Gf9I', '4TWweFic7KA6u4yrm92guH', '3OXayQUy48DyW1ORUVPpoN', '0hK0PTJdd4Jx6Ryl4t8jTi',
          '5vhtS62N7gbH3JPLoD3CoE']

df1 = df1.drop(idx_to_drop)
df1.shape

(19991, 16)

Let's also see what is in the lyrics with a Lyrical score of 2.

In [369]:
low_lyrical_2 = df1[df1['Lyrical']==2] # let's see the rows with a rating of 2 for Lyrical

for index, row in low_lyrical_df_2.iterrows(): 
    print(index)
    print(row['track_lyrics'])
    print("\n ------- \n")

6iC7vapdKp0XlKhxOkp8QJ
Bring that ass back like a boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom

Never give a motherfuck
Boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom

Bring that ass back like a boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, ring that ass back like a boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boom
Boom, boom, boom, boom, boom, boo

011n8lBopxh6VVTxXnyKu0
Fake emcees bore me, it's cool cause unfortunately
Your Georgie Porgie sorority has no authority
This ain't writing, you ain't a killer
So what you gon' do against some niggas who ain't fighting with you
Here's a hint, 11 pop, medics, docs, heaven, god
You know where I'm going with this
You'll be fired from your job cause you rap niggas trynna have a knife fight
Well I brought a firing squad

My nigga Vishis told me spaz, my spit is sharp as bits of broken glass
Pick the biggest chrome to split your dome in half
My clique is so advanced, dope as Ethiopian opium giving dope to cats without sittin' on the ave
Y'all fuckin talk tough, when y'all front and soft ???
When y'all could be as big as Dolph Lundgren, Paul Bunyan
Y'all running when that sawed-off dumping
Like I told this blind broad sucking my dick, I'm the hardest thing you never saw coming
It's all fun and games to me, fly 'til I die
If my plane crash in the ocean, it's plain to see
Shoe G.A.N.G. this psyc

In [373]:
indices_to_drop = ['1bSO9nzT5h55OrJO7BbHL2', '693x7mqPNtiFzJSkFZcB1N', '6ya8ejoKgw906Y8LWclqrp', 
                   '37CGH5jrSVZFFxO602bdq7', '3FygJnwLJbaU5xe4E87h8e', '18Ve6vZ4GaYvZmA1mepYOd',
                  '7f5trao56t7sB7f14QDTmp', '5hM6sP0Gh1jD57drszNueC', '18bWoys4FQwEp9ojZpbH4j',
                  '6EqzQj41ouk0ANwJXCgK6M', '5FmVPVmYN6lKxQpxWf4wIA', '6XHVuErjQ4XNm6nDPVCxVX',
                  '77UjLW8j5UAGAGVGhR5oUK', '0eHFPf7gom9ztF7Jc6FP6C', '3UN6cIn3VIyg0z1LCuFSum',
                  '3Yxmpx64AdWAzG3qAD4Dty']

In [374]:
df1 = df1.drop(indices_to_drop) # drop the indices that are not lyrics
df1.shape

(19975, 16)

In [375]:
df1.to_csv('../datasets/all_ratings_cleaned.csv') # save the data to the same csv (overwrite)